In [0]:
#%pyspark
from pyspark.sql.types import *
from pyspark.sql.functions import *

from pyspark.ml import *
from pyspark.ml.regression import LinearRegression , DecisionTreeRegressor, RandomForestRegressor, GBTRegressionModel, GBTRegressor

from pyspark.ml.feature import VectorAssembler
from pyspark.ml.tuning import ParamGridBuilder, TrainValidationSplit, CrossValidator
from pyspark.ml.evaluation import RegressionEvaluator

from pyspark.ml.feature import VectorIndexer
from pyspark.ml.feature import VectorAssembler, MinMaxScaler
from pyspark.ml.linalg import Vectors

from pyspark.ml.evaluation import BinaryClassificationEvaluator

from pyspark.sql import SparkSession
from pyspark.sql import functions as F

from pyspark.context import SparkContext
from pyspark.mllib.evaluation import MulticlassMetrics


In [0]:
#%pyspark
#PYSPARK_CLI = True
#if PYSPARK_CLI:
	#sc = SparkContext.getOrCreate()
	#spark = SparkSession(sc)

In [0]:
#%pyspark
# File location and type
file_location = "/FileStore/tables/2016_K12Education.csv"
#file_location = "/user/jdang8/2016_K12_Education.csv"
file_type = "csv"

# CSV options
infer_schema = "true"
first_row_is_header = "true"
delimiter = ","

# The applied options are for CSV files. For other file types, these will be ignored.
df = spark.read.format(file_type).option("inferSchema", infer_schema)\
  .option("header", first_row_is_header) \
  .option("sep", delimiter) \
  .load(file_location)

display(df)

In [0]:
#%pyspark
#df.printSchema()

In [0]:
# Create a view or table

temp_table_name = "2016_K12Education_csv"

df.createOrReplaceTempView(temp_table_name)


In [0]:

dftemp=df.select('EmployerName','Position','TotalWages', 'RegularPay', 'MaxPositionSalary', 'MinPositionSalary')
dftemp.show()

+------------+--------------------+----------+----------+-----------------+-----------------+
|EmployerName|            Position|TotalWages|RegularPay|MaxPositionSalary|MinPositionSalary|
+------------+--------------------+----------+----------+-----------------+-----------------+
| ABC Unified|Asst Supt-Academi...|  201382.0|  172700.0|           172700|           172700|
| ABC Unified|Child Care Specia...|      83.0|      83.0|               12|               12|
| ABC Unified|Child Care Specia...|    7152.0|    7152.0|               12|               12|
| ABC Unified|Child Care Specia...|    2664.0|    2664.0|               12|               12|
| ABC Unified|     Counseling Asst|    7755.0|    7755.0|               24|               15|
| ABC Unified|    Director-Schools|  161500.0|  150111.0|           150168|           131856|
| ABC Unified|       Division Asst|   86266.0|   74166.0|            75540|            66312|
| ABC Unified| Grant Support Staff|    3799.0|    3799.0|   

In [0]:
%sql
select * from `2016_K12Education_csv` 

In [0]:
df.take(10)

Out[9]: [Row(Year=2016, EmployerType='K-12 Education', EmployerName='ABC Unified', DepartmentOrSubdivision='Academic Services', Position='Asst Supt-Academic Srvs', ElectedOfficial=False, Judicial=False, OtherPositions=None, MinPositionSalary=172700, MaxPositionSalary=172700, ReportedBaseWage=None, RegularPay=172700.0, OvertimePay=0.0, LumpSumPay=28682, OtherPay=0.0, TotalWages=201382.0, DefinedBenefitPlanContribution=22652, EmployeesRetirementCostCovered=0, DeferredCompensationPlan=4500, HealthDentalVision=17969, TotalRetirementAndHealthContribution=45121, PensionFormula='2 % @ 60', EmployerURL='http://www.abcusd.k12.ca.us/pages/ABC_Unified_School_District/Departments/hr', EmployerPopulation=None, LastUpdatedDate='11/08/2017', EmployerCounty='Los Angeles', SpecialDistrictActivities=None, IncludesUnfundedLiability=None, SpecialDistrictType=None),
 Row(Year=2016, EmployerType='K-12 Education', EmployerName='ABC Unified', DepartmentOrSubdivision='Academic Services', Position='Child Care S

In [0]:
df_sql = spark.sql("select * from 2016_K12Education_csv LIMIT 10")
display(df_sql) 

Year EmployerType EmployerName DepartmentOrSubdivision Position ElectedOfficial Judicial OtherPositions MinPositionSalary MaxPositionSalary ReportedBaseWage RegularPay OvertimePay LumpSumPay OtherPay TotalWages DefinedBenefitPlanContribution EmployeesRetirementCostCovered DeferredCompensationPlan HealthDentalVision TotalRetirementAndHealthContribution PensionFormula EmployerURL EmployerPopulation LastUpdatedDate EmployerCounty SpecialDistrictActivities IncludesUnfundedLiability SpecialDistrictType 2016 K-12 Education ABC Unified Academic Services Asst Supt-Academic Srvs false false null 172700 172700 null 172700.0 0.0 28682 0.0 201382.0 22652 0 4500 17969 45121 2 % @ 60 http://www.abcusd.k12.ca.us/pages/ABC_Unified_School_District/Departments/hr null 11/08/2017 Los Angeles null null null 2016 K-12 Education ABC Unified Academic Services Child Care Specialist false false null 12 12 null 83.0 0.0 0 0.0 83.0 0 0 0 0 0 Non-member http://www.abcusd.k12.ca.us/pages/ABC_Unified_School_District/Departments/hr null 11/08/2017 Los Angeles null null null 2016 K-12 Education ABC Unified Academic Services Child Care Specialist false false Tutor|Tutor|Tutor|Tutor 12 12 null 7152.0 0.0 0 0.0 7152.0 0 0 0 0 0 Non-member http://www.abcusd.k12.ca.us/pages/ABC_Unified_School_District/Departments/hr null 11/08/2017 Los Angeles null null null 2016 K-12 Education ABC Unified Academic Services Child Care Specialist false false Child Care Specialist 12 12 null 2664.0 0.0 0 0.0 2664.0 0 0 0 0 0 Non-member http://www.abcusd.k12.ca.us/pages/ABC_Unified_School_District/Departments/hr null 11/08/2017 Los Angeles null null null 2016 K-12 Education ABC Unified Academic Services Counseling Asst false false null 15 24 null 7755.0 0.0 0 0.0 7755.0 0 0 0 0 0 Non-member http://www.abcusd.k12.ca.us/pages/ABC_Unified_School_District/Departments/hr null 11/08/2017 Los Angeles null null null 2016 K-12 Education ABC Unified Academic Services Director-Schools false false null 131856 150168 null 150111.0 0.0 11389 0.0 161500.0 18530 0 0 15193 33723 2 % @ 60 http://www.abcusd.k12.ca.us/pages/ABC_Unified_School_District/Departments/hr null 11/08/2017 Los Angeles null null null 2016 K-12 Education ABC Unified Academic Services Division Asst false false null 66312 75540 null 74166.0 788.0 11312 0.0 86266.0 10832 0 0 17969 28801 2 % @ 55 http://www.abcusd.k12.ca.us/pages/ABC_Unified_School_District/Departments/hr null 11/08/2017 Los Angeles null null null 2016 K-12 Education ABC Unified Academic Services Grant Support Staff false false Primary Intervention Aide 16 45 null 3799.0 0.0 0 0.0 3799.0 0 0 0 0 0 Non-member http://www.abcusd.k12.ca.us/pages/ABC_Unified_School_District/Departments/hr null 11/08/2017 Los Angeles null null null 2016 K-12 Education ABC Unified Academic Services Health & Safety Aide false false null 35 35 null 1470.0 0.0 0 0.0 1470.0 0 0 0 0 0 Non-member http://www.abcusd.k12.ca.us/pages/ABC_Unified_School_District/Departments/hr null 11/08/2017 Los Angeles null null null 2016 K-12 Education ABC Unified Academic Services Parent Liaison false false Parent Liaison|Noon Supv/Child Care Supv 11 20 null 22230.0 0.0 0 0.0 22230.0 2894 0 0 0 2894 2 % @ 55 http://www.abcusd.k12.ca.us/pages/ABC_Unified_School_District/Departments/hr null 11/08/2017 Los Angeles null null null

In [0]:
df.printSchema()

root
 |-- Year: integer (nullable = true)
 |-- EmployerType: string (nullable = true)
 |-- EmployerName: string (nullable = true)
 |-- DepartmentOrSubdivision: string (nullable = true)
 |-- Position: string (nullable = true)
 |-- ElectedOfficial: boolean (nullable = true)
 |-- Judicial: boolean (nullable = true)
 |-- OtherPositions: string (nullable = true)
 |-- MinPositionSalary: integer (nullable = true)
 |-- MaxPositionSalary: integer (nullable = true)
 |-- ReportedBaseWage: string (nullable = true)
 |-- RegularPay: double (nullable = true)
 |-- OvertimePay: double (nullable = true)
 |-- LumpSumPay: integer (nullable = true)
 |-- OtherPay: double (nullable = true)
 |-- TotalWages: double (nullable = true)
 |-- DefinedBenefitPlanContribution: integer (nullable = true)
 |-- EmployeesRetirementCostCovered: integer (nullable = true)
 |-- DeferredCompensationPlan: integer (nullable = true)
 |-- HealthDentalVision: integer (nullable = true)
 |-- TotalRetirementAndHealthContribution: integ

In [0]:
df2 = df.drop("DepartmentOrSubdivision", "ElectedOfficial", "Judicial","OtherPositions", "DefinedBenefitPlanContribution","EmployeesRetirementCostCovered", "DeferredCompensationPlan","HealthDentalVision", "TotalRetirementAndHealthContribution","PensionFormula", "EmployerURL","EmployerPopulation","IncludesUnfundedLiability", "SpecialDistrictActivities"," IncludesUnfundedLiability","SpecialDistrictType")
df2.printSchema()

root
 |-- Year: integer (nullable = true)
 |-- EmployerType: string (nullable = true)
 |-- EmployerName: string (nullable = true)
 |-- Position: string (nullable = true)
 |-- MinPositionSalary: integer (nullable = true)
 |-- MaxPositionSalary: integer (nullable = true)
 |-- ReportedBaseWage: string (nullable = true)
 |-- RegularPay: double (nullable = true)
 |-- OvertimePay: double (nullable = true)
 |-- LumpSumPay: integer (nullable = true)
 |-- OtherPay: double (nullable = true)
 |-- TotalWages: double (nullable = true)
 |-- LastUpdatedDate: string (nullable = true)
 |-- EmployerCounty: string (nullable = true)



In [0]:
display(df2)

In [0]:
#%pyspark
df3 = df2.na.fill(value=0).na.fill("NA")
df3.show()

+----+--------------+------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|Year|  EmployerType|EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|
+----+--------------+------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|2016|K-12 Education| ABC Unified|Asst Supt-Academi...|           172700|           172700|              NA|  172700.0|        0.0|     28682|     0.0|  201382.0|     11/08/2017|   Los Angeles|
|2016|K-12 Education| ABC Unified|Child Care Specia...|               12|               12|              NA|      83.0|        0.0|         0|     0.0|      83.0|     11/08/2017|   Los Angeles|
|2016|K-12 Education| ABC Unif

In [0]:
splits = df3.randomSplit([0.7,0.3])
train = splits[0]
test = splits[1]
train_rows = train.count()
test_rows = test.count()
print("Training Rows:", train_rows, "Testing Rows:", test_rows)

Training Rows: 466585 Testing Rows: 200064


In [0]:
assembler = VectorAssembler(inputCols = ["RegularPay", "TotalWages","MaxPositionSalary", "MinPositionSalary"], outputCol="wages")

In [0]:
training = assembler.transform(train)
training.show()

+----+--------------+------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+--------------------+
|Year|  EmployerType|EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|               wages|
+----+--------------+------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+--------------------+
|2016|K-12 Education| ABC Unified|1/2 Dept Chair (2...|              771|              771|              NA|   53000.0|        0.0|      1542|     0.0|   54542.0|     11/08/2017|   Los Angeles|[53000.0,54542.0,...|
|2016|K-12 Education| ABC Unified|1/2 Dept Chair (2...|              771|              771|              NA|   57083.0|        0.0|         

#Random Forest Regression

In [0]:
rf = RandomForestRegressor(labelCol="TotalWages", featuresCol="wages", numTrees=10, maxDepth=5)


In [0]:
pipeline = Pipeline(stages=[assembler, rf])

In [0]:
model = pipeline.fit(train)

In [0]:
rfModel = model.stages[-1]
print(rfModel.toDebugString)

In [0]:
#importance column name can be changed

import pandas as pd
featureImp = pd.DataFrame(list(zip(assembler.getInputCols(),
rfModel.featureImportances)),
columns=["trueWages", "importance"])
featureImp.sort_values(by="importance", ascending=False)

trueWages 
 importance 
 
 
 
 
 0 
 RegularPay 
 0.463596 
 
 
 1 
 TotalWages 
 0.405123 
 
 
 3 
 MinPositionSalary 
 0.117876 
 
 
 2 
 MaxPositionSalary 
 0.013404

In [0]:
rf = RandomForestRegressor(labelCol="TotalWages",featuresCol="wages",
numTrees=10, maxDepth=5)
# Combine stages into pipeline
pipeline = Pipeline(stages=[assembler, rf])
model = pipeline.fit(train)

In [0]:
prediction = model.transform(test)
predicted = prediction.select("wages", "prediction", "TotalWages")
predicted.show()

+--------------------+------------------+----------+
|               wages|        prediction|TotalWages|
+--------------------+------------------+----------+
|[57683.0,59225.0,...| 58464.81076136988|   59225.0|
|[65553.0,67095.0,...| 67965.36456825535|   67095.0|
|[69133.0,70675.0,...| 71585.52124182624|   70675.0|
|[84084.0,85626.0,...| 89015.57647424018|   85626.0|
|[92899.0,94441.0,...| 93050.62952269279|   94441.0|
|[95783.0,98096.0,...| 95549.61559423771|   98096.0|
|[98746.0,100288.0...| 98520.09971093002|  100288.0|
|[78959.0,83425.0,...| 89015.57647424018|   83425.0|
|[85486.0,86435.0,...| 89015.57647424018|   86435.0|
|[88394.0,90923.0,...| 90934.91120848352|   90923.0|
|[107359.0,115343....|115052.26861424294|  115343.0|
|[89849.0,96133.0,...| 93433.89728002844|   96133.0|
|[89963.0,94705.0,...| 90934.91120848352|   94705.0|
|[61902.0,63651.0,...|62875.565116207275|   63651.0|
|[82253.0,84002.0,...| 89015.57647424018|   84002.0|
|[86766.0,90264.0,...| 90011.26164762529|   90

In [0]:
display(predicted)

In [0]:
    
      from pyspark.ml.evaluation import RegressionEvaluator
rf_evaluator = RegressionEvaluator(predictionCol="prediction", \
                                   labelCol="TotalWages",metricName="r2")
print("R Squared (R2) on test data = %g" % rf_evaluator.evaluate(prediction))
rf_evaluator = RegressionEvaluator(labelCol="TotalWages", predictionCol="prediction", metricName="rmse")
print("RMSE: %f" % rf_evaluator.evaluate(prediction))

R Squared (R2) on test data = 0.98627
RMSE: 4350.977839


#Gradient Boost Tree (GBT)

In [0]:
#%pyspark
df3 = df2.na.fill(value=0).na.fill("NA")
df3.show()

+----+--------------+------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|Year|  EmployerType|EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|
+----+--------------+------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|2016|K-12 Education| ABC Unified|Asst Supt-Academi...|           172700|           172700|              NA|  172700.0|        0.0|     28682|     0.0|  201382.0|     11/08/2017|   Los Angeles|
|2016|K-12 Education| ABC Unified|Child Care Specia...|               12|               12|              NA|      83.0|        0.0|         0|     0.0|      83.0|     11/08/2017|   Los Angeles|
|2016|K-12 Education| ABC Unif

In [0]:
#%pyspark
splits = df3.randomSplit([0.7,0.3])
train = splits[0]
test = splits[1]
train_rows = train.count()
test_rows = test.count()
print("Training Rows:", train_rows, "Testing Rows:", test_rows)

Training Rows: 466543 Testing Rows: 200106


In [0]:
#%pyspark
assembler = VectorAssembler(inputCols = ["RegularPay", "TotalWages","MaxPositionSalary", "MinPositionSalary"], outputCol="wages")

In [0]:
#%pyspark
training = assembler.transform(train)
training.show()

+----+--------------+------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+--------------------+
|Year|  EmployerType|EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|               wages|
+----+--------------+------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+--------------------+
|2016|K-12 Education| ABC Unified|1/2 Dept Chair (2...|              771|              771|              NA|   53000.0|        0.0|      1542|     0.0|   54542.0|     11/08/2017|   Los Angeles|[53000.0,54542.0,...|
|2016|K-12 Education| ABC Unified|1/2 Dept Chair (2...|              771|              771|              NA|   59141.0|        0.0|      282

In [0]:
#%pyspark

gbt = GBTRegressor(labelCol="TotalWages", featuresCol="wages", maxDepth=5)

In [0]:
#%pyspark
paramGrid = ParamGridBuilder()\
.addGrid(gbt.maxDepth, [2, 5])\
.addGrid(gbt.maxIter, [10, 20])\
.build()

In [0]:
#%pyspark
#gbt_evaluator = RegressionEvaluator(predictionCol="prediction", \ labelCol="TotalWages",metricName="r2")

gbt_evaluator = RegressionEvaluator(predictionCol="prediction", labelCol="TotalWages", metricName="r2")


In [0]:
#%pyspark
pipeline = Pipeline(stages=[assembler, gbt])

In [0]:
#%pyspark
cv = CrossValidator(estimator=pipeline, evaluator= gbt_evaluator, estimatorParamMaps=paramGrid)

In [0]:
#%pyspark
model = cv.fit(train)

In [0]:
#@%pyspark
test.show()


+----+--------------+------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|Year|  EmployerType|EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|
+----+--------------+------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|2016|K-12 Education| ABC Unified|1/2 Dept Chair (2...|              771|              771|              NA|   57083.0|        0.0|         0|     0.0|   57083.0|     11/08/2017|   Los Angeles|
|2016|K-12 Education| ABC Unified|1/2 Dept Chair (2...|              771|              771|              NA|   57683.0|        0.0|      1542|     0.0|   59225.0|     11/08/2017|   Los Angeles|
|2016|K-12 Education| ABC Unif

In [0]:
#%pyspark
prediction = model.transform(test)
predicted = prediction.select("wages", "prediction", "TotalWages")
predicted.show()

+--------------------+------------------+----------+
|               wages|        prediction|TotalWages|
+--------------------+------------------+----------+
|[57083.0,57083.0,...| 58696.48106572502|   57083.0|
|[57683.0,59225.0,...| 58696.48106572502|   59225.0|
|[62598.0,64140.0,...| 64247.35654309314|   64140.0|
|[63727.0,65269.0,...| 64247.35654309314|   65269.0|
|[65619.0,67161.0,...| 66512.73812672863|   67161.0|
|[79775.0,83625.0,...| 83290.69670302392|   83625.0|
|[83044.0,89724.0,...| 87939.42778657757|   89724.0|
|[83400.0,84942.0,...| 83493.49685740612|   84942.0|
|[95783.0,98096.0,...| 97527.98821049825|   98096.0|
|[74320.0,76502.0,...| 77849.36130793413|   76502.0|
|[78959.0,83425.0,...| 83290.69670302392|   83425.0|
|[85486.0,86435.0,...| 87997.63883118043|   86435.0|
|[107359.0,115343....|130012.88084679937|  115343.0|
|[61020.0,62601.0,...| 64247.35654309314|   62601.0|
|[89963.0,94705.0,...| 92561.74740859386|   94705.0|
|[103264.0,104845....|105157.48624101614|  104

In [0]:
#%pyspark
predicted.show()

+--------------------+------------------+----------+
|               wages|        prediction|TotalWages|
+--------------------+------------------+----------+
|[57083.0,57083.0,...| 58696.48106572502|   57083.0|
|[57683.0,59225.0,...| 58696.48106572502|   59225.0|
|[62598.0,64140.0,...| 64247.35654309314|   64140.0|
|[63727.0,65269.0,...| 64247.35654309314|   65269.0|
|[65619.0,67161.0,...| 66512.73812672863|   67161.0|
|[79775.0,83625.0,...| 83290.69670302392|   83625.0|
|[83044.0,89724.0,...| 87939.42778657757|   89724.0|
|[83400.0,84942.0,...| 83493.49685740612|   84942.0|
|[95783.0,98096.0,...| 97527.98821049825|   98096.0|
|[74320.0,76502.0,...| 77849.36130793413|   76502.0|
|[78959.0,83425.0,...| 83290.69670302392|   83425.0|
|[85486.0,86435.0,...| 87997.63883118043|   86435.0|
|[107359.0,115343....|130012.88084679937|  115343.0|
|[61020.0,62601.0,...| 64247.35654309314|   62601.0|
|[89963.0,94705.0,...| 92561.74740859386|   94705.0|
|[103264.0,104845....|105157.48624101614|  104

In [0]:
#%pyspark
print("R Squared (R2) on test data = %g" % gbt_evaluator.evaluate(prediction))
gbt_evaluator = RegressionEvaluator(labelCol="TotalWages", predictionCol="prediction", metricName="rmse")
print("RMSE: %f" % gbt_evaluator.evaluate(prediction))

R Squared (R2) on test data = 0.990972
RMSE: 3522.604463


In [0]:
#%pyspark
cva = TrainValidationSplit(estimator= pipeline, evaluator=gbt_evaluator, estimatorParamMaps=paramGrid, trainRatio=0.8)


example = cva.fit(train)

In [0]:

# Transform the test data and generate predictions by applying the trained model
prediction = example.transform(test)
predicted = prediction.select("wages", "prediction", "TotalWages")
predicted.show()

In [0]:
####CODE BREAK for 2015

#K12-2015

In [0]:
#%pyspark
# File location and type
file_location = "/FileStore/tables/2015_K12Education.csv"
#file_location = "/user/jdang8/2016_UniversityOfCalifornia.csv"
file_type = "csv"

# CSV options
infer_schema = "true"
first_row_is_header = "true"
delimiter = ","

# The applied options are for CSV files. For other file types, these will be ignored.
df = spark.read.format(file_type).option("inferSchema", infer_schema)\
  .option("header", first_row_is_header) \
  .option("sep", delimiter) \
  .load(file_location)

display(df)

Year EmployerType EmployerName DepartmentOrSubdivision Position ElectedOfficial Judicial OtherPositions MinPositionSalary MaxPositionSalary ReportedBaseWage RegularPay OvertimePay LumpSumPay OtherPay TotalWages DefinedBenefitPlanContribution EmployeesRetirementCostCovered DeferredCompensationPlan HealthDentalVision TotalRetirementAndHealthContribution PensionFormula EmployerURL EmployerPopulation LastUpdatedDate EmployerCounty SpecialDistrictActivities IncludesUnfundedLiability SpecialDistrictType 2015 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false Acad Achievement Cnslr 3 0 0 null 52541 0 0 2320 54861 7540 0 0 7782 15322 2.5% @ 65 https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 07/22/2016 Alameda null null null 2015 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false Teacher-Unex 0 0 null 4906 0 0 4140 9046 0 0 0 0 0 N/A https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 07/22/2016 Alameda null null null 2015 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 1126 0 0 0 1126 0 0 0 0 0 N/A https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 07/22/2016 Alameda null null null 2015 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 47593 787 0 500 48880 6663 0 0 7260 13923 2.5% @ 60 https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 07/22/2016 Alameda null null null 2015 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 51624 0 0 0 51624 7227 0 0 7260 14487 2.5% @ 60 https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 07/22/2016 Alameda null null null 2015 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 41739 0 0 0 41739 4449 0 0 16572 21021 2.5% @ 65 https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 07/22/2016 Alameda null null null 2015 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 1058 0 0 0 1058 148 0 0 2170 2318 2.5% @ 65 https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 07/22/2016 Alameda null null null 2015 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 2258 3066 0 2264 7588 316 0 0 0 316 2.5% @ 65 https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 07/22/2016 Alameda null null null 2015 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 48371 275 0 0 48646 6771 0 0 2567 9338 2.5% @ 65 https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 07/22/2016 Alameda null null null 2015 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 47080 0 0 0 47080 3887 0 0 7863 11750 2.5% @ 65 https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 07/22/2016 Alameda null null null 2015 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 28980 0 0 0 28980 1322 0 0 5949 7271 2.5% @ 65 https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 07/22/2016 Alameda null null null 2015 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 24312 0 0 0 24312 3403 0 0 3425 6828 2.5% @ 65 https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 07/22/2016 Alameda null null null 2015 University of California University of California, Berkeley UC - Berkeley Ac

In [0]:
# Create a view or table

temp_table_name = "2015_K12Education_csv"

df.createOrReplaceTempView(temp_table_name)


In [0]:
df2 = df.drop("DepartmentOrSubdivision", "ElectedOfficial", "Judicial","OtherPositions", "DefinedBenefitPlanContribution","EmployeesRetirementCostCovered", "DeferredCompensationPlan","HealthDentalVision", "TotalRetirementAndHealthContribution","PensionFormula", "EmployerURL","EmployerPopulation","IncludesUnfundedLiability", "SpecialDistrictActivities"," IncludesUnfundedLiability","SpecialDistrictType")
df2.printSchema()

root
 |-- Year: integer (nullable = true)
 |-- EmployerType: string (nullable = true)
 |-- EmployerName: string (nullable = true)
 |-- Position: string (nullable = true)
 |-- MinPositionSalary: integer (nullable = true)
 |-- MaxPositionSalary: integer (nullable = true)
 |-- ReportedBaseWage: string (nullable = true)
 |-- RegularPay: integer (nullable = true)
 |-- OvertimePay: integer (nullable = true)
 |-- LumpSumPay: integer (nullable = true)
 |-- OtherPay: integer (nullable = true)
 |-- TotalWages: integer (nullable = true)
 |-- LastUpdatedDate: string (nullable = true)
 |-- EmployerCounty: string (nullable = true)



In [0]:
display(df2)

Year EmployerType EmployerName Position MinPositionSalary MaxPositionSalary ReportedBaseWage RegularPay OvertimePay LumpSumPay OtherPay TotalWages LastUpdatedDate EmployerCounty 2015 University of California University of California, Berkeley Acad Achievement Cnslr 2 0 0 null 52541 0 0 2320 54861 07/22/2016 Alameda 2015 University of California University of California, Berkeley Acad Achievement Cnslr 2 0 0 null 4906 0 0 4140 9046 07/22/2016 Alameda 2015 University of California University of California, Berkeley Acad Achievement Cnslr 2 0 0 null 1126 0 0 0 1126 07/22/2016 Alameda 2015 University of California University of California, Berkeley Acad Achievement Cnslr 2 0 0 null 47593 787 0 500 48880 07/22/2016 Alameda 2015 University of California University of California, Berkeley Acad Achievement Cnslr 2 0 0 null 51624 0 0 0 51624 07/22/2016 Alameda 2015 University of California University of California, Berkeley Acad Achievement Cnslr 2 0 0 null 41739 0 0 0 41739 07/22/2016 Alameda 2015 University of California University of California, Berkeley Acad Achievement Cnslr 2 0 0 null 1058 0 0 0 1058 07/22/2016 Alameda 2015 University of California University of California, Berkeley Acad Achievement Cnslr 2 0 0 null 2258 3066 0 2264 7588 07/22/2016 Alameda 2015 University of California University of California, Berkeley Acad Achievement Cnslr 2 0 0 null 48371 275 0 0 48646 07/22/2016 Alameda 2015 University of California University of California, Berkeley Acad Achievement Cnslr 2 0 0 null 47080 0 0 0 47080 07/22/2016 Alameda 2015 University of California University of California, Berkeley Acad Achievement Cnslr 2 0 0 null 28980 0 0 0 28980 07/22/2016 Alameda 2015 University of California University of California, Berkeley Acad Achievement Cnslr 2 0 0 null 24312 0 0 0 24312 07/22/2016 Alameda 2015 University of California University of California, Berkeley Acad Achievement Cnslr 2 0 0 null 16560 0 0 0 16560 07/22/2016 Alameda 2015 University of California University of California, Berkeley Acad Achievement Cnslr 2 0 0 null 7920 0 0 0 7920 07/22/2016 Alameda 2015 University of California University of California, Berkeley Acad Achievement Cnslr 3 0 0 null 56413 0 0 500 56913 07/22/2016 Alameda 2015 University of California University of California, Berkeley Acad Achievement Cnslr 3 0 0 null 46451 2521 0 2000 50972 07/22/2016 Alameda 2015 University of California University of California, Berkeley Acad Achievement Cnslr 3 0 0 null 56454 0 0 0 56454 07/22/2016 Alameda 2015 University of California University of California, Berkeley Acad Achievement Cnslr 3 0 0 null 57739 0 0 0 57739 07/22/2016 Alameda 2015 University of California University of California, Berkeley Acad Achievement Cnslr 3 0 0 null 76296 0 0 0 76296 07/22/2016 Alameda 2015 University of California University of California, Berkeley Acad Achievement Cnslr 3 0 0 null 58425 0 0 500 58925 07/22/2016 Alameda 2015 University of California University of California, Berkeley Acad Achievement Cnslr 3 0 0 null 51009 0 0 623 51632 07/22/2016 Alameda 2015 University of California University of California, Berkeley Acad Achievement Cnslr 3 0 0 null 58307 0 0 0 58307 07/22/2016 Alameda 2015 University of California University of California, Berkeley Acad Achievement Cnslr 4 0 0 null 86666 0 0 0 86666 07/22/2016 Alameda 2015 University of California University of California, Berkeley Acad Achievement Cnslr 4 0 0 null 63345 0 0 0 63345 07/22/2016 Alameda 2015 University of California University of California, Berkeley Acad Achievement Cnslr 4 0 0 null 61074 0 0 500 61574 07/22/2016 Alameda 2015 University of California University of California, Berkeley Acad Achievement Cnslr 4 0 0 null 48455 0 0 4344 52799 07/22/2016 Alameda 2015 University of California University of California, Berkeley Acad Achievement Cnslr 4 0 0 null 70601 0 0 0 70601 07/22/2016 Alameda 2015 University of California University of California, Berkeley Acad Achievement Cnslr 4 0 0 null 80627 0 0 0 80627 07/22/20

In [0]:
#%pyspark
df3 = df2.na.fill(value=0).na.fill("NA")
df3.show()

+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|Year|        EmployerType|        EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|
+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|2015|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|     52541|          0|         0|    2320|     54861|     07/22/2016|       Alameda|
|2015|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|      4906|          0|         0|    4140|   

In [0]:
splits = df3.randomSplit([0.7,0.3])
train = splits[0]
test = splits[1]
train_rows = train.count()
test_rows = test.count()
print("Training Rows:", train_rows, "Testing Rows:", test_rows)

Training Rows: 197048 Testing Rows: 84467


In [0]:
assembler = VectorAssembler(inputCols = ["RegularPay", "TotalWages","MaxPositionSalary", "MinPositionSalary"], outputCol="wages")

In [0]:
training = assembler.transform(train)
training.show()

+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+--------------------+
|Year|        EmployerType|        EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|               wages|
+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+--------------------+
|2015|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|      1058|          0|         0|       0|      1058|     07/22/2016|       Alameda|[1058.0,1058.0,0....|
|2015|University of Cal...|University of Cal...|Acad Achievement ...|               

#Random Forest Regression

In [0]:
rf = RandomForestRegressor(labelCol="TotalWages", featuresCol="wages", numTrees=10, maxDepth=5)


In [0]:
pipeline = Pipeline(stages=[assembler, rf])

In [0]:
model = pipeline.fit(train)

In [0]:
rfModel = model.stages[-1]
print(rfModel.toDebugString)

RandomForestRegressionModel: uid=RandomForestRegressor_ad06d0df72df, numTrees=10, numFeatures=4
  Tree 0 (weight 1.0):
    If (feature 0 <= 81555.5)
     If (feature 1 <= 30348.0)
      Predict: 8182.269163771543
     Else (feature 1 > 30348.0)
      If (feature 1 <= 62339.0)
       Predict: 46797.0092361516
      Else (feature 1 > 62339.0)
       If (feature 1 <= 140059.5)
        If (feature 0 <= 72124.0)
         Predict: 71333.08088844687
        Else (feature 0 > 72124.0)
         Predict: 81580.06663318265
       Else (feature 1 > 140059.5)
        If (feature 0 <= 16223.0)
         Predict: 285660.6666666667
        Else (feature 0 > 16223.0)
         Predict: 200213.43720930233
    Else (feature 0 > 81555.5)
     Predict: 155489.6939155244
  Tree 1 (weight 1.0):
    If (feature 1 <= 100855.5)
     If (feature 0 <= 33430.5)
      If (feature 0 <= 12470.0)
       Predict: 4237.852031472991
      Else (feature 0 > 12470.0)
       If (feature 1 <= 25479.0)
        Predict: 19036.29

In [0]:
#importance column name can be changed

import pandas as pd
featureImp = pd.DataFrame(list(zip(assembler.getInputCols(),
rfModel.featureImportances)),
columns=["trueWages", "importance"])
featureImp.sort_values(by="importance", ascending=False)

trueWages 
 importance 
 
 
 
 
 0 
 RegularPay 
 0.536837 
 
 
 1 
 TotalWages 
 0.463163 
 
 
 2 
 MaxPositionSalary 
 0.000000 
 
 
 3 
 MinPositionSalary 
 0.000000

In [0]:
rf = RandomForestRegressor(labelCol="TotalWages",featuresCol="wages",
numTrees=10, maxDepth=5)
# Combine stages into pipeline
pipeline = Pipeline(stages=[assembler, rf])
model = pipeline.fit(train)

In [0]:
prediction = model.transform(test)
predicted = prediction.select("wages", "prediction", "TotalWages")
predicted.show()
display(predicted)

+--------------------+------------------+----------+
|               wages|        prediction|TotalWages|
+--------------------+------------------+----------+
|[2258.0,7588.0,0....|17780.043032888694|      7588|
|[4906.0,9046.0,0....|19212.858383994255|      9046|
|[7920.0,7920.0,0....|19562.047760765425|      7920|
|[28980.0,28980.0,...|33663.161941734936|     28980|
|[58425.0,58925.0,...|  54685.4325015431|     58925|
|[44694.0,75319.0,...| 55197.36786671943|     75319|
|[61074.0,61574.0,...|  54685.4325015431|     61574|
|[66806.0,66806.0,...| 63979.46135735682|     66806|
|[68077.0,68577.0,...| 63979.46135735682|     68577|
|[70601.0,70601.0,...| 63979.46135735682|     70601|
|[72701.0,72701.0,...| 65960.67801921938|     72701|
|[76855.0,76855.0,...| 65960.67801921938|     76855|
|[80112.0,80612.0,...| 68337.87304766013|     80612|
|[80180.0,80680.0,...| 68337.87304766013|     80680|
|[80627.0,80627.0,...| 68337.87304766013|     80627|
|[84477.0,84477.0,...| 89189.89859090373|     

wages prediction TotalWages Map(vectorType -> dense, length -> 4, values -> List(2258.0, 7588.0, 0.0, 0.0)) 17780.043032888694 7588 Map(vectorType -> dense, length -> 4, values -> List(4906.0, 9046.0, 0.0, 0.0)) 19212.858383994255 9046 Map(vectorType -> dense, length -> 4, values -> List(7920.0, 7920.0, 0.0, 0.0)) 19562.047760765425 7920 Map(vectorType -> dense, length -> 4, values -> List(28980.0, 28980.0, 0.0, 0.0)) 33663.161941734936 28980 Map(vectorType -> dense, length -> 4, values -> List(58425.0, 58925.0, 0.0, 0.0)) 54685.4325015431 58925 Map(vectorType -> dense, length -> 4, values -> List(44694.0, 75319.0, 0.0, 0.0)) 55197.36786671943 75319 Map(vectorType -> dense, length -> 4, values -> List(61074.0, 61574.0, 0.0, 0.0)) 54685.4325015431 61574 Map(vectorType -> dense, length -> 4, values -> List(66806.0, 66806.0, 0.0, 0.0)) 63979.46135735682 66806 Map(vectorType -> dense, length -> 4, values -> List(68077.0, 68577.0, 0.0, 0.0)) 63979.46135735682 68577 Map(vectorType -> dense, length -> 4, values -> List(70601.0, 70601.0, 0.0, 0.0)) 63979.46135735682 70601 Map(vectorType -> dense, length -> 4, values -> List(72701.0, 72701.0, 0.0, 0.0)) 65960.67801921938 72701 Map(vectorType -> dense, length -> 4, values -> List(76855.0, 76855.0, 0.0, 0.0)) 65960.67801921938 76855 Map(vectorType -> dense, length -> 4, values -> List(80112.0, 80612.0, 0.0, 0.0)) 68337.87304766013 80612 Map(vectorType -> dense, length -> 4, values -> List(80180.0, 80680.0, 0.0, 0.0)) 68337.87304766013 80680 Map(vectorType -> dense, length -> 4, values -> List(80627.0, 80627.0, 0.0, 0.0)) 68337.87304766013 80627 Map(vectorType -> dense, length -> 4, values -> List(84477.0, 84477.0, 0.0, 0.0)) 89189.89859090373 84477 Map(vectorType -> dense, length -> 4, values -> List(92895.0, 93395.0, 0.0, 0.0)) 91427.52615545254 93395 Map(vectorType -> dense, length -> 4, values -> List(83952.0, 83952.0, 0.0, 0.0)) 89189.89859090373 83952 Map(vectorType -> dense, length -> 4, values -> List(90949.0, 96140.0, 0.0, 0.0)) 90217.23528223453 96140 Map(vectorType -> dense, length -> 4, values -> List(57616.0, 58116.0, 0.0, 0.0)) 53952.99577527818 58116 Map(vectorType -> dense, length -> 4, values -> List(58456.0, 58456.0, 0.0, 0.0)) 54685.4325015431 58456 Map(vectorType -> dense, length -> 4, values -> List(60632.0, 61132.0, 0.0, 0.0)) 54685.4325015431 61132 Map(vectorType -> dense, length -> 4, values -> List(60880.0, 61989.0, 0.0, 0.0)) 54685.4325015431 61989 Map(vectorType -> dense, length -> 4, values -> List(61304.0, 62341.0, 0.0, 0.0)) 58603.79004237665 62341 Map(vectorType -> dense, length -> 4, values -> List(63398.0, 63398.0, 0.0, 0.0)) 58603.79004237665 63398 Map(vectorType -> dense, length -> 4, values -> List(64856.0, 68360.0, 0.0, 0.0)) 63979.46135735682 68360 Map(vectorType -> dense, length -> 4, values -> List(65024.0, 65024.0, 0.0, 0.0)) 63979.46135735682 65024 Map(vectorType -> dense, length -> 4, values -> List(69285.0, 69285.0, 0.0, 0.0)) 63979.46135735682 69285 Map(vectorType -> dense, length -> 4, values -> List(41866.0, 50898.0, 0.0, 0.0)) 47477.96953277921 50898 Map(vectorType -> dense, length -> 4, values -> List(52234.0, 52234.0, 0.0, 0.0)) 50630.90075873323 52234 Map(vectorType -> dense, length -> 4, values -> List(57159.0, 60103.0, 0.0, 0.0)) 53952.99577527818 60103 Map(vectorType -> dense, length -> 4, values -> List(61010.0, 61010.0, 0.0, 0.0)) 54685.4325015431 61010 Map(vectorType -> dense, length -> 4, values -> List(62707.0, 62789.0, 0.0, 0.0)) 58603.79004237665 62789 Map(vectorType -> dense, length -> 4, values -> List(68147.0, 68147.0, 0.0, 0.0)) 63979.46135735682 68147 Map(vectorType -> dense, length -> 4, values -> List(69948.0, 73464.0, 0.0, 0.0)) 63979.46135735682 73464 Map(vectorType -> dense, length -> 4, values -> List(75992.0, 75992.0, 0.0, 0.0)) 65960.67801921938 75992 Map(vectorType -> dense, length -> 4, values -> List(76637.0, 76637.0, 0.0, 0.0)) 65960.67801921938 76637 Map(vectorType -> dense, length -> 4, values -> List(77987.0,

In [0]:
    
      from pyspark.ml.evaluation import RegressionEvaluator
rf_evaluator = RegressionEvaluator(predictionCol="prediction", \
                                   labelCol="TotalWages",metricName="r2")
print("R Squared (R2) on test data = %g" % rf_evaluator.evaluate(prediction))
rf_evaluator = RegressionEvaluator(labelCol="TotalWages", predictionCol="prediction", metricName="rmse")
print("RMSE: %f" % rf_evaluator.evaluate(prediction))

R Squared (R2) on test data = 0.703407
RMSE: 36021.903803


In [0]:
#GBT 2015


#Gradient Boost Tree (GBT)

In [0]:
#%pyspark
df3 = df2.na.fill(value=0).na.fill("NA")
df3.show()

+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|Year|        EmployerType|        EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|
+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|2015|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|     52541|          0|         0|    2320|     54861|     07/22/2016|       Alameda|
|2015|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|      4906|          0|         0|    4140|   

In [0]:
#%pyspark
splits = df3.randomSplit([0.7,0.3])
train = splits[0]
test = splits[1]
train_rows = train.count()
test_rows = test.count()
print("Training Rows:", train_rows, "Testing Rows:", test_rows)

Training Rows: 196880 Testing Rows: 84635


In [0]:
#%pyspark
assembler = VectorAssembler(inputCols = ["RegularPay", "TotalWages","MaxPositionSalary", "MinPositionSalary"], outputCol="wages")

In [0]:
#%pyspark
training = assembler.transform(train)
training.show()

+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+--------------------+
|Year|        EmployerType|        EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|               wages|
+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+--------------------+
|2015|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|      1058|          0|         0|       0|      1058|     07/22/2016|       Alameda|[1058.0,1058.0,0....|
|2015|University of Cal...|University of Cal...|Acad Achievement ...|               

In [0]:
#%pyspark

gbt = GBTRegressor(labelCol="TotalWages", featuresCol="wages", maxDepth=5)

In [0]:
#%pyspark
paramGrid = ParamGridBuilder()\
.addGrid(gbt.maxDepth, [2, 5])\
.addGrid(gbt.maxIter, [10, 20])\
.build()

In [0]:
#%pyspark
#gbt_evaluator = RegressionEvaluator(predictionCol="prediction", \ labelCol="TotalWages",metricName="r2")

gbt_evaluator = RegressionEvaluator(predictionCol="prediction", labelCol="TotalWages", metricName="r2")


In [0]:
#%pyspark
pipeline = Pipeline(stages=[assembler, gbt])

In [0]:
#%pyspark
cv = CrossValidator(estimator=pipeline, evaluator= gbt_evaluator, estimatorParamMaps=paramGrid)

In [0]:
#%pyspark
model = cv.fit(train)

In [0]:
#%pyspark
prediction = model.transform(test)
predicted = prediction.select("wages", "prediction", "TotalWages")
predicted.show()

+--------------------+------------------+----------+
|               wages|        prediction|TotalWages|
+--------------------+------------------+----------+
|[2258.0,7588.0,0....| 8760.982824037097|      7588|
|[47080.0,47080.0,...| 46887.07132172138|     47080|
|[51624.0,51624.0,...| 50602.41902599607|     51624|
|[57739.0,57739.0,...| 57997.31090092057|     57739|
|[72701.0,72701.0,...| 72761.84876912097|     72701|
|[76855.0,76855.0,...| 81182.21119351551|     76855|
|[76855.0,76855.0,...| 81182.21119351551|     76855|
|[80112.0,80612.0,...| 81182.21119351551|     80612|
|[80180.0,80680.0,...| 81182.21119351551|     80680|
|[80627.0,80627.0,...| 81182.21119351551|     80627|
|[81346.0,81846.0,...| 82524.08929304755|     81846|
|[84477.0,84477.0,...| 82524.08929304755|     84477|
|[69490.0,151496.0...| 159071.9481881537|    151496|
|[106884.0,106884....|112157.69650128376|    106884|
|[123655.0,123655....|133306.44156796802|    123655|
|[74989.0,74989.0,...| 72761.84876912097|     

In [0]:
#%pyspark
predicted.show()

+--------------------+------------------+----------+
|               wages|        prediction|TotalWages|
+--------------------+------------------+----------+
|[2258.0,7588.0,0....| 8760.982824037097|      7588|
|[47080.0,47080.0,...| 46887.07132172138|     47080|
|[51624.0,51624.0,...| 50602.41902599607|     51624|
|[57739.0,57739.0,...| 57997.31090092057|     57739|
|[72701.0,72701.0,...| 72761.84876912097|     72701|
|[76855.0,76855.0,...| 81182.21119351551|     76855|
|[76855.0,76855.0,...| 81182.21119351551|     76855|
|[80112.0,80612.0,...| 81182.21119351551|     80612|
|[80180.0,80680.0,...| 81182.21119351551|     80680|
|[80627.0,80627.0,...| 81182.21119351551|     80627|
|[81346.0,81846.0,...| 82524.08929304755|     81846|
|[84477.0,84477.0,...| 82524.08929304755|     84477|
|[69490.0,151496.0...| 159071.9481881537|    151496|
|[106884.0,106884....|112157.69650128376|    106884|
|[123655.0,123655....|133306.44156796802|    123655|
|[74989.0,74989.0,...| 72761.84876912097|     

In [0]:
#%pyspark
print("R Squared (R2) on test data = %g" % gbt_evaluator.evaluate(prediction))
gbt_evaluator = RegressionEvaluator(labelCol="TotalWages", predictionCol="prediction", metricName="rmse")
print("RMSE: %f" % gbt_evaluator.evaluate(prediction))

R Squared (R2) on test data = 0.838996
RMSE: 26479.379164


In [0]:
#%pyspark
cva = TrainValidationSplit(estimator= pipeline, evaluator=gbt_evaluator, estimatorParamMaps=paramGrid, trainRatio=0.8)


example = cva.fit(train)

In [0]:

# Transform the test data and generate predictions by applying the trained model
prediction = example.transform(test)
predicted = prediction.select("wages", "prediction", "TotalWages")
predicted.show()

+--------------------+------------------+----------+
|               wages|        prediction|TotalWages|
+--------------------+------------------+----------+
|[2258.0,7588.0,0....| 8760.982824037097|      7588|
|[47080.0,47080.0,...| 46887.07132172138|     47080|
|[51624.0,51624.0,...| 50602.41902599607|     51624|
|[57739.0,57739.0,...| 57997.31090092057|     57739|
|[72701.0,72701.0,...| 72761.84876912097|     72701|
|[76855.0,76855.0,...| 81182.21119351551|     76855|
|[76855.0,76855.0,...| 81182.21119351551|     76855|
|[80112.0,80612.0,...| 81182.21119351551|     80612|
|[80180.0,80680.0,...| 81182.21119351551|     80680|
|[80627.0,80627.0,...| 81182.21119351551|     80627|
|[81346.0,81846.0,...| 82524.08929304755|     81846|
|[84477.0,84477.0,...| 82524.08929304755|     84477|
|[69490.0,151496.0...| 159071.9481881537|    151496|
|[106884.0,106884....|112157.69650128376|    106884|
|[123655.0,123655....|133306.44156796802|    123655|
|[74989.0,74989.0,...| 72761.84876912097|     

In [0]:
#### Code Break for 2017

#K12-2017

In [0]:
#%pyspark
# File location and type
file_location = "/FileStore/tables/2017_K12Education.csv"
#file_location = "/user/jdang8/2017_UniversityOfCalifornia.csv"
file_type = "csv"

# CSV options
infer_schema = "true"
first_row_is_header = "true"
delimiter = ","

# The applied options are for CSV files. For other file types, these will be ignored.
df = spark.read.format(file_type).option("inferSchema", infer_schema)\
  .option("header", first_row_is_header) \
  .option("sep", delimiter) \
  .load(file_location)

display(df)

Year EmployerType EmployerName DepartmentOrSubdivision Position ElectedOfficial Judicial OtherPositions MinPositionSalary MaxPositionSalary ReportedBaseWage RegularPay OvertimePay LumpSumPay OtherPay TotalWages DefinedBenefitPlanContribution EmployeesRetirementCostCovered DeferredCompensationPlan HealthDentalVision TotalRetirementAndHealthContribution PensionFormula EmployerURL EmployerPopulation LastUpdatedDate EmployerCounty SpecialDistrictActivities IncludesUnfundedLiability SpecialDistrictType 2017 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false Tut-Non Gship 0 0 null 14572 0 0 500 15072 0 0 0 0 0 null https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/25/2018 Alameda null true null 2017 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 15283 376 0 0 15659 1835 0 0 4226 6061 2016 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/25/2018 Alameda null true null 2017 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 27410 0 0 500 27910 3837 0 0 12386 16223 2016 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/25/2018 Alameda null true null 2017 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 3410 0 0 0 3410 0 0 0 0 0 null https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/25/2018 Alameda null true null 2017 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 6215 0 0 0 6215 0 0 0 1295 1295 N/A https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/25/2018 Alameda null true null 2017 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false Stdt 4 0 0 null 20064 0 0 1000 21064 0 0 0 0 0 null https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/25/2018 Alameda null true null 2017 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 48176 1313 0 0 49489 5132 0 0 15000 20132 2016 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/25/2018 Alameda null true null 2017 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 4004 0 0 0 4004 0 0 0 0 0 null https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/25/2018 Alameda null true null 2017 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 51220 0 0 0 51220 7170 0 0 25099 32269 2013 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/25/2018 Alameda null true null 2017 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 9438 0 0 0 9438 0 0 0 2035 2035 N/A https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/25/2018 Alameda null true null 2017 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 31039 0 0 0 31039 4345 0 0 4610 8955 2013 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/25/2018 Alameda null true null 2017 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 49638 386 0 500 50524 6949 0 0 9080 16029 2013 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/25/2018 Alameda null true null 2017 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 6193 0 

In [0]:
# Create a view or table

temp_table_name = "2017_K12Education_csv"

df.createOrReplaceTempView(temp_table_name)


In [0]:
df2 = df.drop("DepartmentOrSubdivision", "ElectedOfficial", "Judicial","OtherPositions", "DefinedBenefitPlanContribution","EmployeesRetirementCostCovered", "DeferredCompensationPlan","HealthDentalVision", "TotalRetirementAndHealthContribution","PensionFormula", "EmployerURL","EmployerPopulation","IncludesUnfundedLiability", "SpecialDistrictActivities"," IncludesUnfundedLiability","SpecialDistrictType")
df2.printSchema()

root
 |-- Year: integer (nullable = true)
 |-- EmployerType: string (nullable = true)
 |-- EmployerName: string (nullable = true)
 |-- Position: string (nullable = true)
 |-- MinPositionSalary: integer (nullable = true)
 |-- MaxPositionSalary: integer (nullable = true)
 |-- ReportedBaseWage: string (nullable = true)
 |-- RegularPay: integer (nullable = true)
 |-- OvertimePay: integer (nullable = true)
 |-- LumpSumPay: integer (nullable = true)
 |-- OtherPay: integer (nullable = true)
 |-- TotalWages: integer (nullable = true)
 |-- LastUpdatedDate: string (nullable = true)
 |-- EmployerCounty: string (nullable = true)



In [0]:
#%pyspark
df3 = df2.na.fill(value=0).na.fill("NA")
df3.show()

+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|Year|        EmployerType|        EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|
+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|2017|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|     14572|          0|         0|     500|     15072|     09/25/2018|       Alameda|
|2017|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|     15283|        376|         0|       0|   

In [0]:
splits = df3.randomSplit([0.7,0.3])
train = splits[0]
test = splits[1]
train_rows = train.count()
test_rows = test.count()
print("Training Rows:", train_rows, "Testing Rows:", test_rows)

Training Rows: 208807 Testing Rows: 89259


In [0]:
assembler = VectorAssembler(inputCols = ["RegularPay", "TotalWages","MaxPositionSalary", "MinPositionSalary"], outputCol="wages")

In [0]:
training = assembler.transform(train)
training.show()

+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+--------------------+
|Year|        EmployerType|        EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|               wages|
+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+--------------------+
|2017|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|      3410|          0|         0|       0|      3410|     09/25/2018|       Alameda|[3410.0,3410.0,0....|
|2017|University of Cal...|University of Cal...|Acad Achievement ...|               

#Random Forest Regression

In [0]:
rf = RandomForestRegressor(labelCol="TotalWages", featuresCol="wages", numTrees=10, maxDepth=5)


In [0]:
pipeline = Pipeline(stages=[assembler, rf])

In [0]:
model = pipeline.fit(train)

In [0]:
rfModel = model.stages[-1]
print(rfModel.toDebugString)

RandomForestRegressionModel: uid=RandomForestRegressor_0412e16ba1d1, numTrees=10, numFeatures=4
  Tree 0 (weight 1.0):
    If (feature 0 <= 91687.5)
     If (feature 1 <= 33596.0)
      Predict: 9020.694680666038
     Else (feature 1 > 33596.0)
      If (feature 1 <= 68981.0)
       Predict: 51367.46573884917
      Else (feature 1 > 68981.0)
       If (feature 1 <= 158485.5)
        If (feature 0 <= 80354.0)
         Predict: 79404.61194149149
        Else (feature 0 > 80354.0)
         Predict: 91794.97842657845
       Else (feature 1 > 158485.5)
        If (feature 0 <= 36624.0)
         Predict: 451683.875
        Else (feature 0 > 36624.0)
         Predict: 224391.2902097902
    Else (feature 0 > 91687.5)
     Predict: 172326.5172651285
  Tree 1 (weight 1.0):
    If (feature 1 <= 114986.5)
     If (feature 0 <= 36624.0)
      If (feature 0 <= 13302.5)
       Predict: 4552.296395501043
      Else (feature 0 > 13302.5)
       If (feature 1 <= 28063.5)
        Predict: 20774.974121188

In [0]:
#importance column name can be changed

import pandas as pd
featureImp = pd.DataFrame(list(zip(assembler.getInputCols(),
rfModel.featureImportances)),
columns=["trueWages", "importance"])
featureImp.sort_values(by="importance", ascending=False)

trueWages 
 importance 
 
 
 
 
 0 
 RegularPay 
 0.532456 
 
 
 1 
 TotalWages 
 0.467544 
 
 
 2 
 MaxPositionSalary 
 0.000000 
 
 
 3 
 MinPositionSalary 
 0.000000

In [0]:
rf = RandomForestRegressor(labelCol="TotalWages",featuresCol="wages",
numTrees=10, maxDepth=5)
# Combine stages into pipeline
pipeline = Pipeline(stages=[assembler, rf])
model = pipeline.fit(train)

In [0]:
prediction = model.transform(test)
predicted = prediction.select("wages", "prediction", "TotalWages")
predicted.show()

+--------------------+------------------+----------+
|               wages|        prediction|TotalWages|
+--------------------+------------------+----------+
|[4004.0,4004.0,0....| 18321.63562644492|      4004|
|[53643.0,54143.0,...|53768.807121001904|     54143|
|[38717.0,39230.0,...| 48626.50155424628|     39230|
|[50218.0,50440.0,...| 53077.77289163355|     50440|
|[53366.0,54366.0,...|53768.807121001904|     54366|
|[63588.0,63588.0,...| 60130.72615271479|     63588|
|[66196.0,66196.0,...| 60970.24923590083|     66196|
|[84020.0,84020.0,...| 74651.45192327096|     84020|
|[91125.0,91125.0,...|  76070.3709031197|     91125|
|[23891.0,78551.0,...| 56034.37235511919|     78551|
|[91061.0,92061.0,...|  76070.3709031197|     92061|
|[109731.0,119336....|119221.89788479109|    119336|
|[145597.0,153097....|131723.37991242975|    153097|
|[80971.0,81471.0,...| 74651.45192327096|     81471|
|[47196.0,47196.0,...| 52182.49711380289|     47196|
|[60674.0,61644.0,...| 60130.72615271479|     

In [0]:
display(predicted)

wages prediction TotalWages Map(vectorType -> dense, length -> 4, values -> List(4004.0, 4004.0, 0.0, 0.0)) 18321.63562644492 4004 Map(vectorType -> dense, length -> 4, values -> List(53643.0, 54143.0, 0.0, 0.0)) 53768.807121001904 54143 Map(vectorType -> dense, length -> 4, values -> List(38717.0, 39230.0, 0.0, 0.0)) 48626.50155424628 39230 Map(vectorType -> dense, length -> 4, values -> List(50218.0, 50440.0, 0.0, 0.0)) 53077.77289163355 50440 Map(vectorType -> dense, length -> 4, values -> List(53366.0, 54366.0, 0.0, 0.0)) 53768.807121001904 54366 Map(vectorType -> dense, length -> 4, values -> List(63588.0, 63588.0, 0.0, 0.0)) 60130.72615271479 63588 Map(vectorType -> dense, length -> 4, values -> List(66196.0, 66196.0, 0.0, 0.0)) 60970.24923590083 66196 Map(vectorType -> dense, length -> 4, values -> List(84020.0, 84020.0, 0.0, 0.0)) 74651.45192327096 84020 Map(vectorType -> dense, length -> 4, values -> List(91125.0, 91125.0, 0.0, 0.0)) 76070.3709031197 91125 Map(vectorType -> dense, length -> 4, values -> List(23891.0, 78551.0, 0.0, 0.0)) 56034.37235511919 78551 Map(vectorType -> dense, length -> 4, values -> List(91061.0, 92061.0, 0.0, 0.0)) 76070.3709031197 92061 Map(vectorType -> dense, length -> 4, values -> List(109731.0, 119336.0, 0.0, 0.0)) 119221.89788479109 119336 Map(vectorType -> dense, length -> 4, values -> List(145597.0, 153097.0, 0.0, 0.0)) 131723.37991242975 153097 Map(vectorType -> dense, length -> 4, values -> List(80971.0, 81471.0, 0.0, 0.0)) 74651.45192327096 81471 Map(vectorType -> dense, length -> 4, values -> List(47196.0, 47196.0, 0.0, 0.0)) 52182.49711380289 47196 Map(vectorType -> dense, length -> 4, values -> List(60674.0, 61644.0, 0.0, 0.0)) 60130.72615271479 61644 Map(vectorType -> dense, length -> 4, values -> List(62893.0, 62893.0, 0.0, 0.0)) 60130.72615271479 62893 Map(vectorType -> dense, length -> 4, values -> List(68109.0, 68141.0, 0.0, 0.0)) 60970.24923590083 68141 Map(vectorType -> dense, length -> 4, values -> List(69293.0, 69293.0, 0.0, 0.0)) 66395.81845960942 69293 Map(vectorType -> dense, length -> 4, values -> List(71256.0, 71773.0, 0.0, 0.0)) 66395.81845960942 71773 Map(vectorType -> dense, length -> 4, values -> List(4406.0, 4406.0, 0.0, 0.0)) 18321.63562644492 4406 Map(vectorType -> dense, length -> 4, values -> List(23913.0, 23913.0, 0.0, 0.0)) 31111.4650143463 23913 Map(vectorType -> dense, length -> 4, values -> List(45441.0, 52810.0, 0.0, 0.0)) 51451.255719726614 52810 Map(vectorType -> dense, length -> 4, values -> List(50435.0, 52136.0, 0.0, 0.0)) 53077.77289163355 52136 Map(vectorType -> dense, length -> 4, values -> List(62954.0, 62954.0, 0.0, 0.0)) 60130.72615271479 62954 Map(vectorType -> dense, length -> 4, values -> List(68173.0, 68173.0, 0.0, 0.0)) 60970.24923590083 68173 Map(vectorType -> dense, length -> 4, values -> List(69312.0, 69812.0, 0.0, 0.0)) 66395.81845960942 69812 Map(vectorType -> dense, length -> 4, values -> List(75605.0, 75605.0, 0.0, 0.0)) 70595.55478549177 75605 Map(vectorType -> dense, length -> 4, values -> List(76926.0, 79328.0, 0.0, 0.0)) 71522.3287057367 79328 Map(vectorType -> dense, length -> 4, values -> List(77220.0, 77220.0, 0.0, 0.0)) 71522.3287057367 77220 Map(vectorType -> dense, length -> 4, values -> List(83911.0, 85407.0, 0.0, 0.0)) 74651.45192327096 85407 Map(vectorType -> dense, length -> 4, values -> List(89136.0, 89636.0, 0.0, 0.0)) 76070.3709031197 89636 Map(vectorType -> dense, length -> 4, values -> List(19565.0, 19565.0, 0.0, 0.0)) 28520.960300587194 19565 Map(vectorType -> dense, length -> 4, values -> List(93503.0, 94003.0, 0.0, 0.0)) 99090.14783299032 94003 Map(vectorType -> dense, length -> 4, values -> List(94290.0, 94290.0, 0.0, 0.0)) 99090.14783299032 94290 Map(vectorType -> dense, length -> 4, values -> List(96744.0, 97244.0, 0.0, 0.0)) 99090.14783299032 97244 Map(vectorType -> dense, length -> 4, values -> List(98381.0, 98881.0, 0.0, 0.0)) 101888.89515725004 98881 Map(vectorType -> dense, length -> 4, values -> L

In [0]:
    
      from pyspark.ml.evaluation import RegressionEvaluator
rf_evaluator = RegressionEvaluator(predictionCol="prediction", \
                                   labelCol="TotalWages",metricName="r2")
print("R Squared (R2) on test data = %g" % rf_evaluator.evaluate(prediction))
rf_evaluator = RegressionEvaluator(labelCol="TotalWages", predictionCol="prediction", metricName="rmse")
print("RMSE: %f" % rf_evaluator.evaluate(prediction))

R Squared (R2) on test data = 0.736294
RMSE: 36007.523494


#Gradient Boost Tree (GBT)

In [0]:
#%pyspark
df3 = df2.na.fill(value=0).na.fill("NA")
df3.show()

+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|Year|        EmployerType|        EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|
+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|2017|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|     14572|          0|         0|     500|     15072|     09/25/2018|       Alameda|
|2017|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|     15283|        376|         0|       0|   

In [0]:
#%pyspark
splits = df3.randomSplit([0.7,0.3])
train = splits[0]
test = splits[1]
train_rows = train.count()
test_rows = test.count()
print("Training Rows:", train_rows, "Testing Rows:", test_rows)

Training Rows: 208361 Testing Rows: 89705


In [0]:
#%pyspark
assembler = VectorAssembler(inputCols = ["RegularPay", "TotalWages","MaxPositionSalary", "MinPositionSalary"], outputCol="wages")

In [0]:
#%pyspark
training = assembler.transform(train)
training.show()

+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+--------------------+
|Year|        EmployerType|        EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|               wages|
+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+--------------------+
|2017|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|      3410|          0|         0|       0|      3410|     09/25/2018|       Alameda|[3410.0,3410.0,0....|
|2017|University of Cal...|University of Cal...|Acad Achievement ...|               

In [0]:
#%pyspark

gbt = GBTRegressor(labelCol="TotalWages", featuresCol="wages", maxDepth=5)

In [0]:
#%pyspark
paramGrid = ParamGridBuilder()\
.addGrid(gbt.maxDepth, [2, 5])\
.addGrid(gbt.maxIter, [10, 20])\
.build()

In [0]:
#%pyspark
#gbt_evaluator = RegressionEvaluator(predictionCol="prediction", \ labelCol="TotalWages",metricName="r2")

gbt_evaluator = RegressionEvaluator(predictionCol="prediction", labelCol="TotalWages", metricName="r2")


In [0]:
#%pyspark
pipeline = Pipeline(stages=[assembler, gbt])

In [0]:
#%pyspark
cv = CrossValidator(estimator=pipeline, evaluator= gbt_evaluator, estimatorParamMaps=paramGrid)

In [0]:
#%pyspark
model = cv.fit(train)

In [0]:
#@%pyspark
test.show()


+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|Year|        EmployerType|        EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|
+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|2017|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|     14572|          0|         0|     500|     15072|     09/25/2018|       Alameda|
|2017|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|     49638|        386|         0|     500|   

In [0]:
#%pyspark
prediction = model.transform(test)
predicted = prediction.select("wages", "prediction", "TotalWages")
predicted.show()

+--------------------+------------------+----------+
|               wages|        prediction|TotalWages|
+--------------------+------------------+----------+
|[14572.0,15072.0,...| 17285.09328566919|     15072|
|[49638.0,50524.0,...|50223.389337318295|     50524|
|[51220.0,51220.0,...| 51093.87530548458|     51220|
|[53643.0,54143.0,...|  55520.4789431136|     54143|
|[31487.0,31487.0,...|30723.193289748822|     31487|
|[73718.0,73718.0,...|  73099.3362765826|     73718|
|[76125.0,76125.0,...|  73099.3362765826|     76125|
|[90168.0,90168.0,...| 92370.61775147523|     90168|
|[23891.0,78551.0,...| 80631.78303791507|     78551|
|[72396.0,73396.0,...|  73099.3362765826|     73396|
|[45224.0,51812.0,...|50223.389337318295|     51812|
|[100245.0,103245....|102178.56377234348|    103245|
|[53364.0,53864.0,...|  55520.4789431136|     53864|
|[60255.0,60255.0,...|59924.598477649335|     60255|
|[75681.0,76181.0,...|  73099.3362765826|     76181|
|[4406.0,4406.0,0....| 4511.230970451439|     

In [0]:
#%pyspark
predicted.show()

+--------------------+------------------+----------+
|               wages|        prediction|TotalWages|
+--------------------+------------------+----------+
|[14572.0,15072.0,...| 17285.09328566919|     15072|
|[49638.0,50524.0,...|50223.389337318295|     50524|
|[51220.0,51220.0,...| 51093.87530548458|     51220|
|[53643.0,54143.0,...|  55520.4789431136|     54143|
|[31487.0,31487.0,...|30723.193289748822|     31487|
|[73718.0,73718.0,...|  73099.3362765826|     73718|
|[76125.0,76125.0,...|  73099.3362765826|     76125|
|[90168.0,90168.0,...| 92370.61775147523|     90168|
|[23891.0,78551.0,...| 80631.78303791507|     78551|
|[72396.0,73396.0,...|  73099.3362765826|     73396|
|[45224.0,51812.0,...|50223.389337318295|     51812|
|[100245.0,103245....|102178.56377234348|    103245|
|[53364.0,53864.0,...|  55520.4789431136|     53864|
|[60255.0,60255.0,...|59924.598477649335|     60255|
|[75681.0,76181.0,...|  73099.3362765826|     76181|
|[4406.0,4406.0,0....| 4511.230970451439|     

In [0]:
#%pyspark
print("R Squared (R2) on test data = %g" % gbt_evaluator.evaluate(prediction))
gbt_evaluator = RegressionEvaluator(labelCol="TotalWages", predictionCol="prediction", metricName="rmse")
print("RMSE: %f" % gbt_evaluator.evaluate(prediction))

R Squared (R2) on test data = 0.855818
RMSE: 26865.270234


In [0]:
#%pyspark
cva = TrainValidationSplit(estimator= pipeline, evaluator=gbt_evaluator, estimatorParamMaps=paramGrid, trainRatio=0.8)


example = cva.fit(train)

In [0]:

# Transform the test data and generate predictions by applying the trained model
prediction = example.transform(test)
predicted = prediction.select("wages", "prediction", "TotalWages")
predicted.show()

+--------------------+------------------+----------+
|               wages|        prediction|TotalWages|
+--------------------+------------------+----------+
|[14572.0,15072.0,...| 17285.09328566919|     15072|
|[49638.0,50524.0,...|50223.389337318295|     50524|
|[51220.0,51220.0,...| 51093.87530548458|     51220|
|[53643.0,54143.0,...|  55520.4789431136|     54143|
|[31487.0,31487.0,...|30723.193289748822|     31487|
|[73718.0,73718.0,...|  73099.3362765826|     73718|
|[76125.0,76125.0,...|  73099.3362765826|     76125|
|[90168.0,90168.0,...| 92370.61775147523|     90168|
|[23891.0,78551.0,...| 80631.78303791507|     78551|
|[72396.0,73396.0,...|  73099.3362765826|     73396|
|[45224.0,51812.0,...|50223.389337318295|     51812|
|[100245.0,103245....|102178.56377234348|    103245|
|[53364.0,53864.0,...|  55520.4789431136|     53864|
|[60255.0,60255.0,...|59924.598477649335|     60255|
|[75681.0,76181.0,...|  73099.3362765826|     76181|
|[4406.0,4406.0,0....| 4511.230970451439|     

In [0]:
# Code Break for 2018

#K12-2018

In [0]:
#%pyspark
# File location and type
file_location = "/FileStore/tables/2018_K12Education.csv"
#file_location = "/user/jdang8/2018_UniversityOfCalifornia.csv"
file_type = "csv"

# CSV options
infer_schema = "true"
first_row_is_header = "true"
delimiter = ","

# The applied options are for CSV files. For other file types, these will be ignored.
df = spark.read.format(file_type).option("inferSchema", infer_schema)\
  .option("header", first_row_is_header) \
  .option("sep", delimiter) \
  .load(file_location)

display(df)

Year EmployerType EmployerName DepartmentOrSubdivision Position ElectedOfficial Judicial OtherPositions MinPositionSalary MaxPositionSalary ReportedBaseWage RegularPay OvertimePay LumpSumPay OtherPay TotalWages DefinedBenefitPlanContribution EmployeesRetirementCostCovered DeferredCompensationPlan HealthDentalVision TotalRetirementAndHealthContribution PensionFormula EmployerURL EmployerPopulation LastUpdatedDate EmployerCounty SpecialDistrictActivities IncludesUnfundedLiability SpecialDistrictType 2018 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false Tut-Gship 0 0 null 13794 456 0 0 14250 0 0 0 0 0 null https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/24/2019 Alameda null false null 2018 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false Admissions Evaluator 3 0 0 null 39328 3931 0 2080 45339 3273 0 0 18273 21546 2016 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/24/2019 Alameda null false null 2018 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 29257 0 0 0 29257 2341 0 0 6982 9323 2016 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/24/2019 Alameda null false null 2018 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 3208 0 0 0 3208 0 0 0 403 403 N/A https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/24/2019 Alameda null false null 2018 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 32868 542 0 2471 35881 2629 0 0 9171 11800 2016 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/24/2019 Alameda null false null 2018 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 51335 0 0 0 51335 3148 0 0 9818 12966 2016 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/24/2019 Alameda null false null 2018 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false Admissions Evaluator 3 0 0 null 6174 0 0 652 6826 0 0 0 0 0 null https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/24/2019 Alameda null false null 2018 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false Stdt 3 0 0 null 14760 0 0 0 14760 0 0 0 773 773 2016 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/24/2019 Alameda null false null 2018 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 52810 310 0 500 53620 4225 0 0 25489 29714 2013 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/24/2019 Alameda null false null 2018 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 3 false false Lect-Ay|Teacher-Unex|Lect In Summer Session|Lect-Ay-1/10 0 0 null 49035 0 0 29033 78068 3923 0 217 6429 10569 2013 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/24/2019 Alameda null false null 2018 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 3 false false Admissions Recrmt Spec 3 0 0 null 69647 0 0 0 69647 5572 0 0 13223 18795 2013 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/24/2019 Alameda null false null 2018 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 3 false false Acad Achievement Cnslr 2 0 0 null 58822 0 0 0 58822 4706 0 0 6335 11041 2013 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benef

In [0]:
# Create a view or table

temp_table_name = "2018_K12Education_csv"

df.createOrReplaceTempView(temp_table_name)


In [0]:
df2 = df.drop("DepartmentOrSubdivision", "ElectedOfficial", "Judicial","OtherPositions", "DefinedBenefitPlanContribution","EmployeesRetirementCostCovered", "DeferredCompensationPlan","HealthDentalVision", "TotalRetirementAndHealthContribution","PensionFormula", "EmployerURL","EmployerPopulation","IncludesUnfundedLiability", "SpecialDistrictActivities"," IncludesUnfundedLiability","SpecialDistrictType")
df2.printSchema()

root
 |-- Year: integer (nullable = true)
 |-- EmployerType: string (nullable = true)
 |-- EmployerName: string (nullable = true)
 |-- Position: string (nullable = true)
 |-- MinPositionSalary: integer (nullable = true)
 |-- MaxPositionSalary: integer (nullable = true)
 |-- ReportedBaseWage: string (nullable = true)
 |-- RegularPay: integer (nullable = true)
 |-- OvertimePay: integer (nullable = true)
 |-- LumpSumPay: integer (nullable = true)
 |-- OtherPay: integer (nullable = true)
 |-- TotalWages: integer (nullable = true)
 |-- LastUpdatedDate: string (nullable = true)
 |-- EmployerCounty: string (nullable = true)



In [0]:
#%pyspark
df3 = df2.na.fill(value=0).na.fill("NA")
df3.show()

+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|Year|        EmployerType|        EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|
+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|2018|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|     13794|        456|         0|       0|     14250|     09/24/2019|       Alameda|
|2018|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|     39328|       3931|         0|    2080|   

In [0]:
splits = df3.randomSplit([0.7,0.3])
train = splits[0]
test = splits[1]
train_rows = train.count()
test_rows = test.count()
print("Training Rows:", train_rows, "Testing Rows:", test_rows)

Training Rows: 213967 Testing Rows: 92040


In [0]:
assembler = VectorAssembler(inputCols = ["RegularPay", "TotalWages","MaxPositionSalary", "MinPositionSalary"], outputCol="wages")

In [0]:
training = assembler.transform(train)
training.show()

+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+--------------------+
|Year|        EmployerType|        EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|               wages|
+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+--------------------+
|2018|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|      3208|          0|         0|       0|      3208|     09/24/2019|       Alameda|[3208.0,3208.0,0....|
|2018|University of Cal...|University of Cal...|Acad Achievement ...|               

#Random Forest Regression

In [0]:
rf = RandomForestRegressor(labelCol="TotalWages", featuresCol="wages", numTrees=10, maxDepth=5)


In [0]:
pipeline = Pipeline(stages=[assembler, rf])

In [0]:
model = pipeline.fit(train)

In [0]:
rfModel = model.stages[-1]
print(rfModel.toDebugString)

RandomForestRegressionModel: uid=RandomForestRegressor_89579db4b5dc, numTrees=10, numFeatures=4
  Tree 0 (weight 1.0):
    If (feature 0 <= 94136.5)
     If (feature 1 <= 40147.0)
      Predict: 10833.23448913546
     Else (feature 1 > 40147.0)
      If (feature 1 <= 70971.0)
       Predict: 54943.33777982586
      Else (feature 1 > 70971.0)
       If (feature 1 <= 133482.0)
        If (feature 0 <= 83520.5)
         Predict: 81099.52216098734
        Else (feature 0 > 83520.5)
         Predict: 94370.37118744447
       Else (feature 1 > 133482.0)
        If (feature 0 <= 6.0)
         Predict: 399067.1
        Else (feature 0 > 6.0)
         Predict: 182175.69923371647
    Else (feature 0 > 94136.5)
     Predict: 175927.148992139
  Tree 1 (weight 1.0):
    If (feature 1 <= 115320.5)
     If (feature 0 <= 37772.5)
      If (feature 0 <= 14060.0)
       Predict: 4682.336788534659
      Else (feature 0 > 14060.0)
       If (feature 1 <= 28880.0)
        Predict: 21670.95751130547
       

In [0]:
#importance column name can be changed

import pandas as pd
featureImp = pd.DataFrame(list(zip(assembler.getInputCols(),
rfModel.featureImportances)),
columns=["trueWages", "importance"])
featureImp.sort_values(by="importance", ascending=False)

trueWages 
 importance 
 
 
 
 
 0 
 RegularPay 
 0.534996 
 
 
 1 
 TotalWages 
 0.465004 
 
 
 2 
 MaxPositionSalary 
 0.000000 
 
 
 3 
 MinPositionSalary 
 0.000000

In [0]:
rf = RandomForestRegressor(labelCol="TotalWages",featuresCol="wages",
numTrees=10, maxDepth=5)
# Combine stages into pipeline
pipeline = Pipeline(stages=[assembler, rf])
model = pipeline.fit(train)

In [0]:
prediction = model.transform(test)
predicted = prediction.select("wages", "prediction", "TotalWages")
predicted.show()
display(predicted)

+--------------------+------------------+----------+
|               wages|        prediction|TotalWages|
+--------------------+------------------+----------+
|[6174.0,6826.0,0....|20890.232274225757|      6826|
|[14760.0,14760.0,...|26836.944156814425|     14760|
|[4246.0,4246.0,0....|19166.228064987903|      4246|
|[19842.0,20181.0,...| 30058.82615650903|     20181|
|[49035.0,78068.0,...|59511.570299012994|     78068|
|[63305.0,64305.0,...|61473.433904853286|     64305|
|[67152.0,67152.0,...|63473.551937629396|     67152|
|[69647.0,69647.0,...|63473.551937629396|     69647|
|[77607.0,77607.0,...| 71419.92766403036|     77607|
|[79216.0,79216.0,...| 72417.67199629647|     79216|
|[86492.0,86992.0,...| 77330.88311335744|     86992|
|[93948.0,93948.0,...| 78734.38569730101|     93948|
|[90655.0,91155.0,...| 78734.38569730101|     91155|
|[108077.0,108077....|105262.60790913517|    108077|
|     (4,[1],[693.0])|18242.832202691072|       693|
|[25060.0,27098.0,...|31622.406537679526|     

wages prediction TotalWages Map(vectorType -> dense, length -> 4, values -> List(6174.0, 6826.0, 0.0, 0.0)) 20890.232274225757 6826 Map(vectorType -> dense, length -> 4, values -> List(14760.0, 14760.0, 0.0, 0.0)) 26836.944156814425 14760 Map(vectorType -> dense, length -> 4, values -> List(4246.0, 4246.0, 0.0, 0.0)) 19166.228064987903 4246 Map(vectorType -> dense, length -> 4, values -> List(19842.0, 20181.0, 0.0, 0.0)) 30058.82615650903 20181 Map(vectorType -> dense, length -> 4, values -> List(49035.0, 78068.0, 0.0, 0.0)) 59511.570299012994 78068 Map(vectorType -> dense, length -> 4, values -> List(63305.0, 64305.0, 0.0, 0.0)) 61473.433904853286 64305 Map(vectorType -> dense, length -> 4, values -> List(67152.0, 67152.0, 0.0, 0.0)) 63473.551937629396 67152 Map(vectorType -> dense, length -> 4, values -> List(69647.0, 69647.0, 0.0, 0.0)) 63473.551937629396 69647 Map(vectorType -> dense, length -> 4, values -> List(77607.0, 77607.0, 0.0, 0.0)) 71419.92766403036 77607 Map(vectorType -> dense, length -> 4, values -> List(79216.0, 79216.0, 0.0, 0.0)) 72417.67199629647 79216 Map(vectorType -> dense, length -> 4, values -> List(86492.0, 86992.0, 0.0, 0.0)) 77330.88311335744 86992 Map(vectorType -> dense, length -> 4, values -> List(93948.0, 93948.0, 0.0, 0.0)) 78734.38569730101 93948 Map(vectorType -> dense, length -> 4, values -> List(90655.0, 91155.0, 0.0, 0.0)) 78734.38569730101 91155 Map(vectorType -> dense, length -> 4, values -> List(108077.0, 108077.0, 0.0, 0.0)) 105262.60790913517 108077 Map(vectorType -> sparse, length -> 4, indices -> List(1), values -> List(693.0)) 18242.832202691072 693 Map(vectorType -> dense, length -> 4, values -> List(25060.0, 27098.0, 0.0, 0.0)) 31622.406537679526 27098 Map(vectorType -> dense, length -> 4, values -> List(61966.0, 62466.0, 0.0, 0.0)) 61473.433904853286 62466 Map(vectorType -> dense, length -> 4, values -> List(67229.0, 67229.0, 0.0, 0.0)) 63473.551937629396 67229 Map(vectorType -> dense, length -> 4, values -> List(69455.0, 69455.0, 0.0, 0.0)) 63473.551937629396 69455 Map(vectorType -> dense, length -> 4, values -> List(1197.0, 1197.0, 0.0, 0.0)) 18242.832202691072 1197 Map(vectorType -> dense, length -> 4, values -> List(13125.0, 17662.0, 0.0, 0.0)) 26065.93182892409 17662 Map(vectorType -> dense, length -> 4, values -> List(47821.0, 48321.0, 0.0, 0.0)) 53168.10114644751 48321 Map(vectorType -> dense, length -> 4, values -> List(68850.0, 68850.0, 0.0, 0.0)) 63473.551937629396 68850 Map(vectorType -> dense, length -> 4, values -> List(70686.0, 70686.0, 0.0, 0.0)) 63473.551937629396 70686 Map(vectorType -> dense, length -> 4, values -> List(75176.0, 75176.0, 0.0, 0.0)) 71419.92766403036 75176 Map(vectorType -> dense, length -> 4, values -> List(76589.0, 77089.0, 0.0, 0.0)) 71419.92766403036 77089 Map(vectorType -> dense, length -> 4, values -> List(79151.0, 79651.0, 0.0, 0.0)) 72417.67199629647 79651 Map(vectorType -> dense, length -> 4, values -> List(59260.0, 59260.0, 0.0, 0.0)) 57174.54306887525 59260 Map(vectorType -> dense, length -> 4, values -> List(85784.0, 88399.0, 0.0, 0.0)) 77330.88311335744 88399 Map(vectorType -> dense, length -> 4, values -> List(94464.0, 94964.0, 0.0, 0.0)) 101340.10146220494 94964 Map(vectorType -> dense, length -> 4, values -> List(98146.0, 98646.0, 0.0, 0.0)) 101340.10146220494 98646 Map(vectorType -> dense, length -> 4, values -> List(117023.0, 117023.0, 0.0, 0.0)) 121005.34341031662 117023 Map(vectorType -> dense, length -> 4, values -> List(127752.0, 127752.0, 0.0, 0.0)) 126110.05636875945 127752 Map(vectorType -> dense, length -> 4, values -> List(19832.0, 19832.0, 0.0, 0.0)) 29540.85883248346 19832 Map(vectorType -> dense, length -> 4, values -> List(141750.0, 141750.0, 0.0, 0.0)) 133551.07855078502 141750 Map(vectorType -> dense, length -> 4, values -> List(104355.0, 104855.0, 0.0, 0.0)) 104567.82786181122 104855 Map(vectorType -> dense, length -> 4, values -> List(127705.0, 128205.0, 0.0, 0.0)) 126110.05636875945 128205 Map(vectorType -> de

In [0]:
    
      from pyspark.ml.evaluation import RegressionEvaluator
rf_evaluator = RegressionEvaluator(predictionCol="prediction", \
                                   labelCol="TotalWages",metricName="r2")
print("R Squared (R2) on test data = %g" % rf_evaluator.evaluate(prediction))
rf_evaluator = RegressionEvaluator(labelCol="TotalWages", predictionCol="prediction", metricName="rmse")
print("RMSE: %f" % rf_evaluator.evaluate(prediction))

R Squared (R2) on test data = 0.731247
RMSE: 37667.488888


#Gradient Boost Tree (GBT)

In [0]:
#%pyspark
df3 = df2.na.fill(value=0).na.fill("NA")
df3.show()

+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|Year|        EmployerType|        EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|
+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|2018|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|     13794|        456|         0|       0|     14250|     09/24/2019|       Alameda|
|2018|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|     39328|       3931|         0|    2080|   

In [0]:
#%pyspark
splits = df3.randomSplit([0.7,0.3])
train = splits[0]
test = splits[1]
train_rows = train.count()
test_rows = test.count()
print("Training Rows:", train_rows, "Testing Rows:", test_rows)

Training Rows: 213908 Testing Rows: 92099


In [0]:
#%pyspark
assembler = VectorAssembler(inputCols = ["RegularPay", "TotalWages","MaxPositionSalary", "MinPositionSalary"], outputCol="wages")

In [0]:
#%pyspark
training = assembler.transform(train)
training.show()

+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+--------------------+
|Year|        EmployerType|        EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|               wages|
+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+--------------------+
|2018|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|     32868|        542|         0|    2471|     35881|     09/24/2019|       Alameda|[32868.0,35881.0,...|
|2018|University of Cal...|University of Cal...|Acad Achievement ...|               

In [0]:
#%pyspark

gbt = GBTRegressor(labelCol="TotalWages", featuresCol="wages", maxDepth=5)

In [0]:
#%pyspark
paramGrid = ParamGridBuilder()\
.addGrid(gbt.maxDepth, [2, 5])\
.addGrid(gbt.maxIter, [10, 20])\
.build()

In [0]:
#%pyspark
#gbt_evaluator = RegressionEvaluator(predictionCol="prediction", \ labelCol="TotalWages",metricName="r2")

gbt_evaluator = RegressionEvaluator(predictionCol="prediction", labelCol="TotalWages", metricName="r2")


In [0]:
#%pyspark
pipeline = Pipeline(stages=[assembler, gbt])

In [0]:
#%pyspark
cv = CrossValidator(estimator=pipeline, evaluator= gbt_evaluator, estimatorParamMaps=paramGrid)

In [0]:
#%pyspark
model = cv.fit(train)

In [0]:
#@%pyspark
test.show()


+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|Year|        EmployerType|        EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|
+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|2018|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|      3208|          0|         0|       0|      3208|     09/24/2019|       Alameda|
|2018|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|      6174|          0|         0|     652|   

In [0]:
#%pyspark
prediction = model.transform(test)
predicted = prediction.select("wages", "prediction", "TotalWages")
predicted.show()

+--------------------+------------------+----------+
|               wages|        prediction|TotalWages|
+--------------------+------------------+----------+
|[3208.0,3208.0,0....| 3501.499426314903|      3208|
|[6174.0,6826.0,0....| 8008.227843850768|      6826|
|[13794.0,14250.0,...|13131.186889275697|     14250|
|[14760.0,14760.0,...|13797.420676311556|     14760|
|[29257.0,29257.0,...| 30818.63976628121|     29257|
|[51335.0,51335.0,...| 50952.30662893921|     51335|
|[19842.0,20181.0,...|20732.864573872794|     20181|
|[39101.0,39101.0,...|41550.089599245715|     39101|
|[43531.0,46373.0,...| 47250.64673929777|     46373|
|[62546.0,63046.0,...|  61299.5665709841|     63046|
|[65354.0,65354.0,...| 66116.84061986613|     65354|
|[25521.0,25521.0,...|26045.902084261757|     25521|
|[72685.0,76770.0,...| 73503.43969824843|     76770|
|[86492.0,86992.0,...|  85322.0933349848|     86992|
|[93859.0,93859.0,...| 98355.65554895902|     93859|
|[93948.0,93948.0,...| 98355.65554895902|     

In [0]:
#%pyspark
predicted.show()

+--------------------+------------------+----------+
|               wages|        prediction|TotalWages|
+--------------------+------------------+----------+
|[3208.0,3208.0,0....| 3501.499426314903|      3208|
|[6174.0,6826.0,0....| 8008.227843850768|      6826|
|[13794.0,14250.0,...|13131.186889275697|     14250|
|[14760.0,14760.0,...|13797.420676311556|     14760|
|[29257.0,29257.0,...| 30818.63976628121|     29257|
|[51335.0,51335.0,...| 50952.30662893921|     51335|
|[19842.0,20181.0,...|20732.864573872794|     20181|
|[39101.0,39101.0,...|41550.089599245715|     39101|
|[43531.0,46373.0,...| 47250.64673929777|     46373|
|[62546.0,63046.0,...|  61299.5665709841|     63046|
|[65354.0,65354.0,...| 66116.84061986613|     65354|
|[25521.0,25521.0,...|26045.902084261757|     25521|
|[72685.0,76770.0,...| 73503.43969824843|     76770|
|[86492.0,86992.0,...|  85322.0933349848|     86992|
|[93859.0,93859.0,...| 98355.65554895902|     93859|
|[93948.0,93948.0,...| 98355.65554895902|     

In [0]:
#%pyspark
print("R Squared (R2) on test data = %g" % gbt_evaluator.evaluate(prediction))
gbt_evaluator = RegressionEvaluator(labelCol="TotalWages", predictionCol="prediction", metricName="rmse")
print("RMSE: %f" % gbt_evaluator.evaluate(prediction))

R Squared (R2) on test data = 0.874567
RMSE: 25486.684664


In [0]:
#%pyspark
cva = TrainValidationSplit(estimator= pipeline, evaluator=gbt_evaluator, estimatorParamMaps=paramGrid, trainRatio=0.8)


example = cva.fit(train)

In [0]:

# Transform the test data and generate predictions by applying the trained model
prediction = example.transform(test)
predicted = prediction.select("wages", "prediction", "TotalWages")
predicted.show()

+--------------------+------------------+----------+
|               wages|        prediction|TotalWages|
+--------------------+------------------+----------+
|[3208.0,3208.0,0....| 3501.499426314903|      3208|
|[6174.0,6826.0,0....| 8008.227843850768|      6826|
|[13794.0,14250.0,...|13131.186889275697|     14250|
|[14760.0,14760.0,...|13797.420676311556|     14760|
|[29257.0,29257.0,...| 30818.63976628121|     29257|
|[51335.0,51335.0,...| 50952.30662893921|     51335|
|[19842.0,20181.0,...|20732.864573872794|     20181|
|[39101.0,39101.0,...|41550.089599245715|     39101|
|[43531.0,46373.0,...| 47250.64673929777|     46373|
|[62546.0,63046.0,...|  61299.5665709841|     63046|
|[65354.0,65354.0,...| 66116.84061986613|     65354|
|[25521.0,25521.0,...|26045.902084261757|     25521|
|[72685.0,76770.0,...| 73503.43969824843|     76770|
|[86492.0,86992.0,...|  85322.0933349848|     86992|
|[93859.0,93859.0,...| 98355.65554895902|     93859|
|[93948.0,93948.0,...| 98355.65554895902|     

In [0]:
### Code Break for 2019

#K12-2019

In [0]:
#%pyspark
# File location and type
file_location = "/FileStore/tables/2019_K12Education.csv"
#file_location = "/user/jdang8/2016_UniversityOfCalifornia.csv"
file_type = "csv"

# CSV options
infer_schema = "true"
first_row_is_header = "true"
delimiter = ","

# The applied options are for CSV files. For other file types, these will be ignored.
df = spark.read.format(file_type).option("inferSchema", infer_schema)\
  .option("header", first_row_is_header) \
  .option("sep", delimiter) \
  .load(file_location)

display(df)

Year EmployerType EmployerName DepartmentOrSubdivision Position ElectedOfficial Judicial OtherPositions MinPositionSalary MaxPositionSalary ReportedBaseWage RegularPay OvertimePay LumpSumPay OtherPay TotalWages DefinedBenefitPlanContribution EmployeesRetirementCostCovered DeferredCompensationPlan HealthDentalVision TotalRetirementAndHealthContribution PensionFormula EmployerURL EmployerPopulation LastUpdatedDate EmployerCounty SpecialDistrictActivities IncludesUnfundedLiability SpecialDistrictType 2019 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false Stdt 3|Teachg Asst-1/10-Gship 0 0 null 28780 17 0 0 28797 0 0 0 0 0 null https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 10/13/2020 Alameda null false null 2019 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 30656 198 0 549 31403 1642 0 0 1641 3283 2016 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 10/13/2020 Alameda null false null 2019 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 19543 0 0 0 19543 841 0 0 8169 9010 2016 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 10/13/2020 Alameda null false null 2019 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false Admissions Evaluator 3 0 0 null 46179 0 0 3205 49384 2578 0 0 20633 23211 2016 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 10/13/2020 Alameda null false null 2019 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 5154 0 0 0 5154 0 0 0 0 0 null https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 10/13/2020 Alameda null false null 2019 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 56923 0 0 2000 58923 3034 0 0 9199 12233 N/A https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 10/13/2020 Alameda null false null 2019 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 24552 0 0 626 25178 0 0 0 875 875 N/A https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 10/13/2020 Alameda null false null 2019 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 21842 0 0 0 21842 999 0 0 2805 3804 N/A https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 10/13/2020 Alameda null false null 2019 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false Admissions Evaluator 3 0 0 null 15618 0 0 0 15618 0 0 0 1860 1860 N/A https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 10/13/2020 Alameda null false null 2019 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false Acad Achievement Cnslr 3 0 0 null 56162 0 0 5015 61177 4894 0 0 23636 28530 2013 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 10/13/2020 Alameda null false null 2019 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 39770 22 0 500 40292 2046 0 0 7270 9316 2016 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 10/13/2020 Alameda null false null 2019 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 6568 0 0 0 6568 0 0 0 1175 1175 N/A https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 10/13/2020 Alameda null false null 2019 University of California University of Cal

In [0]:
# Create a view or table

temp_table_name = "2019_K12Education_csv"

df.createOrReplaceTempView(temp_table_name)


In [0]:
df2 = df.drop("DepartmentOrSubdivision", "ElectedOfficial", "Judicial","OtherPositions", "DefinedBenefitPlanContribution","EmployeesRetirementCostCovered", "DeferredCompensationPlan","HealthDentalVision", "TotalRetirementAndHealthContribution","PensionFormula", "EmployerURL","EmployerPopulation","IncludesUnfundedLiability", "SpecialDistrictActivities"," IncludesUnfundedLiability","SpecialDistrictType")
df2.printSchema()

root
 |-- Year: integer (nullable = true)
 |-- EmployerType: string (nullable = true)
 |-- EmployerName: string (nullable = true)
 |-- Position: string (nullable = true)
 |-- MinPositionSalary: integer (nullable = true)
 |-- MaxPositionSalary: integer (nullable = true)
 |-- ReportedBaseWage: string (nullable = true)
 |-- RegularPay: integer (nullable = true)
 |-- OvertimePay: integer (nullable = true)
 |-- LumpSumPay: integer (nullable = true)
 |-- OtherPay: integer (nullable = true)
 |-- TotalWages: integer (nullable = true)
 |-- LastUpdatedDate: string (nullable = true)
 |-- EmployerCounty: string (nullable = true)



In [0]:
#%pyspark
df3 = df2.na.fill(value=0).na.fill("NA")
df3.show()

+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|Year|        EmployerType|        EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|
+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|2019|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|     28780|         17|         0|       0|     28797|     10/13/2020|       Alameda|
|2019|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|     30656|        198|         0|     549|   

In [0]:
splits = df3.randomSplit([0.7,0.3])
train = splits[0]
test = splits[1]
train_rows = train.count()
test_rows = test.count()
print("Training Rows:", train_rows, "Testing Rows:", test_rows)

Training Rows: 218402 Testing Rows: 93716


In [0]:
assembler = VectorAssembler(inputCols = ["RegularPay", "TotalWages","MaxPositionSalary", "MinPositionSalary"], outputCol="wages")

In [0]:
training = assembler.transform(train)
training.show()

+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+--------------------+
|Year|        EmployerType|        EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|               wages|
+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+--------------------+
|2019|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|      5154|          0|         0|       0|      5154|     10/13/2020|       Alameda|[5154.0,5154.0,0....|
|2019|University of Cal...|University of Cal...|Acad Achievement ...|               

#Random Forest Regression

In [0]:
rf = RandomForestRegressor(labelCol="TotalWages", featuresCol="wages", numTrees=10, maxDepth=5)


In [0]:
pipeline = Pipeline(stages=[assembler, rf])
model = pipeline.fit(train)

In [0]:
rfModel = model.stages[-1]
print(rfModel.toDebugString)

RandomForestRegressionModel: uid=RandomForestRegressor_b534f9272593, numTrees=10, numFeatures=4
  Tree 0 (weight 1.0):
    If (feature 0 <= 98089.5)
     If (feature 1 <= 36189.0)
      Predict: 10094.554368642057
     Else (feature 1 > 36189.0)
      If (feature 1 <= 72867.5)
       Predict: 54177.03419995421
      Else (feature 1 > 72867.5)
       If (feature 1 <= 141846.0)
        If (feature 0 <= 85824.5)
         Predict: 83451.15358668765
        Else (feature 0 > 85824.5)
         Predict: 97394.55391120508
       Else (feature 1 > 141846.0)
        If (feature 0 <= 53528.5)
         Predict: 272079.8333333333
        Else (feature 0 > 53528.5)
         Predict: 192983.2275862069
    Else (feature 0 > 98089.5)
     Predict: 185811.05585580322
  Tree 1 (weight 1.0):
    If (feature 1 <= 121506.0)
     If (feature 0 <= 39013.5)
      If (feature 0 <= 15349.0)
       Predict: 5160.593455039367
      Else (feature 0 > 15349.0)
       If (feature 1 <= 31066.5)
        Predict: 23506.

In [0]:
#importance column name can be changed

import pandas as pd
featureImp = pd.DataFrame(list(zip(assembler.getInputCols(),
rfModel.featureImportances)),
columns=["trueWages", "importance"])
featureImp.sort_values(by="importance", ascending=False)

trueWages 
 importance 
 
 
 
 
 0 
 RegularPay 
 0.530359 
 
 
 1 
 TotalWages 
 0.469641 
 
 
 2 
 MaxPositionSalary 
 0.000000 
 
 
 3 
 MinPositionSalary 
 0.000000

In [0]:
rf = RandomForestRegressor(labelCol="TotalWages",featuresCol="wages",
numTrees=10, maxDepth=5)
# Combine stages into pipeline
pipeline = Pipeline(stages=[assembler, rf])
model = pipeline.fit(train)

In [0]:
prediction = model.transform(test)
predicted = prediction.select("wages", "prediction", "TotalWages")
predicted.show()
display(predicted)

+--------------------+------------------+----------+
|               wages|        prediction|TotalWages|
+--------------------+------------------+----------+
|[24552.0,25178.0,...|31258.330117311627|     25178|
|[30656.0,31403.0,...| 36850.95936831949|     31403|
|[38632.0,38632.0,...| 46885.71085722052|     38632|
|[56923.0,58923.0,...|  57154.0833324739|     58923|
|[40304.0,45988.0,...| 54357.61281570264|     45988|
|[61525.0,63525.0,...| 59951.05411047019|     63525|
|[66002.0,68002.0,...| 62915.74816638008|     68002|
|[67880.0,67880.0,...| 62915.74816638008|     67880|
|[68889.0,68889.0,...| 63848.92798469977|     68889|
|[68977.0,68977.0,...| 63848.92798469977|     68977|
|[82537.0,84537.0,...| 75757.01525228587|     84537|
|[83103.0,85103.0,...| 75757.01525228587|     85103|
|[85296.0,86296.0,...| 75757.01525228587|     86296|
|[94090.0,94090.0,...| 81282.13932058259|     94090|
|[100192.0,107231....|107438.07883856868|    107231|
|[91567.0,91567.0,...| 81282.13932058259|     

wages prediction TotalWages Map(vectorType -> dense, length -> 4, values -> List(24552.0, 25178.0, 0.0, 0.0)) 31258.330117311627 25178 Map(vectorType -> dense, length -> 4, values -> List(30656.0, 31403.0, 0.0, 0.0)) 36850.95936831949 31403 Map(vectorType -> dense, length -> 4, values -> List(38632.0, 38632.0, 0.0, 0.0)) 46885.71085722052 38632 Map(vectorType -> dense, length -> 4, values -> List(56923.0, 58923.0, 0.0, 0.0)) 57154.0833324739 58923 Map(vectorType -> dense, length -> 4, values -> List(40304.0, 45988.0, 0.0, 0.0)) 54357.61281570264 45988 Map(vectorType -> dense, length -> 4, values -> List(61525.0, 63525.0, 0.0, 0.0)) 59951.05411047019 63525 Map(vectorType -> dense, length -> 4, values -> List(66002.0, 68002.0, 0.0, 0.0)) 62915.74816638008 68002 Map(vectorType -> dense, length -> 4, values -> List(67880.0, 67880.0, 0.0, 0.0)) 62915.74816638008 67880 Map(vectorType -> dense, length -> 4, values -> List(68889.0, 68889.0, 0.0, 0.0)) 63848.92798469977 68889 Map(vectorType -> dense, length -> 4, values -> List(68977.0, 68977.0, 0.0, 0.0)) 63848.92798469977 68977 Map(vectorType -> dense, length -> 4, values -> List(82537.0, 84537.0, 0.0, 0.0)) 75757.01525228587 84537 Map(vectorType -> dense, length -> 4, values -> List(83103.0, 85103.0, 0.0, 0.0)) 75757.01525228587 85103 Map(vectorType -> dense, length -> 4, values -> List(85296.0, 86296.0, 0.0, 0.0)) 75757.01525228587 86296 Map(vectorType -> dense, length -> 4, values -> List(94090.0, 94090.0, 0.0, 0.0)) 81282.13932058259 94090 Map(vectorType -> dense, length -> 4, values -> List(100192.0, 107231.0, 0.0, 0.0)) 107438.07883856868 107231 Map(vectorType -> dense, length -> 4, values -> List(91567.0, 91567.0, 0.0, 0.0)) 81282.13932058259 91567 Map(vectorType -> dense, length -> 4, values -> List(95013.0, 96013.0, 0.0, 0.0)) 81282.13932058259 96013 Map(vectorType -> dense, length -> 4, values -> List(106724.0, 106724.0, 0.0, 0.0)) 107438.07883856868 106724 Map(vectorType -> dense, length -> 4, values -> List(111832.0, 112832.0, 0.0, 0.0)) 108294.75846818757 112832 Map(vectorType -> dense, length -> 4, values -> List(118257.0, 119257.0, 0.0, 0.0)) 108294.75846818757 119257 Map(vectorType -> dense, length -> 4, values -> List(94328.0, 95328.0, 0.0, 0.0)) 81282.13932058259 95328 Map(vectorType -> dense, length -> 4, values -> List(57451.0, 57951.0, 0.0, 0.0)) 57154.0833324739 57951 Map(vectorType -> dense, length -> 4, values -> List(64846.0, 67346.0, 0.0, 0.0)) 62915.74816638008 67346 Map(vectorType -> dense, length -> 4, values -> List(69795.0, 70795.0, 0.0, 0.0)) 63848.92798469977 70795 Map(vectorType -> dense, length -> 4, values -> List(72378.0, 72878.0, 0.0, 0.0)) 68647.11082352244 72878 Map(vectorType -> dense, length -> 4, values -> List(72708.0, 73208.0, 0.0, 0.0)) 68647.11082352244 73208 Map(vectorType -> dense, length -> 4, values -> List(75470.0, 75470.0, 0.0, 0.0)) 68647.11082352244 75470 Map(vectorType -> dense, length -> 4, values -> List(75940.0, 75940.0, 0.0, 0.0)) 74989.18556620902 75940 Map(vectorType -> dense, length -> 4, values -> List(77177.0, 77177.0, 0.0, 0.0)) 74989.18556620902 77177 Map(vectorType -> dense, length -> 4, values -> List(79297.0, 83181.0, 0.0, 0.0)) 75757.01525228587 83181 Map(vectorType -> dense, length -> 4, values -> List(82098.0, 82598.0, 0.0, 0.0)) 75757.01525228587 82598 Map(vectorType -> dense, length -> 4, values -> List(85886.0, 88570.0, 0.0, 0.0)) 78385.6746276605 88570 Map(vectorType -> dense, length -> 4, values -> List(86633.0, 86633.0, 0.0, 0.0)) 78385.6746276605 86633 Map(vectorType -> dense, length -> 4, values -> List(94875.0, 94875.0, 0.0, 0.0)) 81282.13932058259 94875 Map(vectorType -> dense, length -> 4, values -> List(100874.0, 105041.0, 0.0, 0.0)) 107438.07883856868 105041 Map(vectorType -> dense, length -> 4, values -> List(14610.0, 14610.0, 0.0, 0.0)) 24580.859429970493 14610 Map(vectorType -> dense, length -> 4, values -> List(131662.0, 141662.0, 0.0, 0.0)) 128726.48379477602 141662 Map(vectorType -> dense, len

In [0]:
    
      from pyspark.ml.evaluation import RegressionEvaluator
rf_evaluator = RegressionEvaluator(predictionCol="prediction", \
                                   labelCol="TotalWages",metricName="r2")
print("R Squared (R2) on test data = %g" % rf_evaluator.evaluate(prediction))
rf_evaluator = RegressionEvaluator(labelCol="TotalWages", predictionCol="prediction", metricName="rmse")
print("RMSE: %f" % rf_evaluator.evaluate(prediction))

R Squared (R2) on test data = 0.745072
RMSE: 37811.234799


#Gradient Boost Tree (GBT)

In [0]:
#%pyspark
df3 = df2.na.fill(value=0).na.fill("NA")
df3.show()

+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|Year|        EmployerType|        EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|
+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|2019|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|     28780|         17|         0|       0|     28797|     10/13/2020|       Alameda|
|2019|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|     30656|        198|         0|     549|   

In [0]:
#%pyspark
splits = df3.randomSplit([0.7,0.3])
train = splits[0]
test = splits[1]
train_rows = train.count()
test_rows = test.count()
print("Training Rows:", train_rows, "Testing Rows:", test_rows)

Training Rows: 218151 Testing Rows: 93967


In [0]:
#%pyspark
assembler = VectorAssembler(inputCols = ["RegularPay", "TotalWages","MaxPositionSalary", "MinPositionSalary"], outputCol="wages")

In [0]:
#%pyspark
training = assembler.transform(train)
training.show()

+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+--------------------+
|Year|        EmployerType|        EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|               wages|
+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+--------------------+
|2019|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|      5154|          0|         0|       0|      5154|     10/13/2020|       Alameda|[5154.0,5154.0,0....|
|2019|University of Cal...|University of Cal...|Acad Achievement ...|               

In [0]:
#%pyspark

gbt = GBTRegressor(labelCol="TotalWages", featuresCol="wages", maxDepth=5)

In [0]:
#%pyspark
paramGrid = ParamGridBuilder()\
.addGrid(gbt.maxDepth, [2, 5])\
.addGrid(gbt.maxIter, [10, 20])\
.build()

In [0]:
#%pyspark
#gbt_evaluator = RegressionEvaluator(predictionCol="prediction", \ labelCol="TotalWages",metricName="r2")

gbt_evaluator = RegressionEvaluator(predictionCol="prediction", labelCol="TotalWages", metricName="r2")


In [0]:
#%pyspark
pipeline = Pipeline(stages=[assembler, gbt])

In [0]:
#%pyspark
cv = CrossValidator(estimator=pipeline, evaluator= gbt_evaluator, estimatorParamMaps=paramGrid)

In [0]:
#%pyspark
model = cv.fit(train)

test.show()


+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|Year|        EmployerType|        EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|
+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|2019|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|      6568|          0|         0|       0|      6568|     10/13/2020|       Alameda|
|2019|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|     19543|          0|         0|       0|   

In [0]:
#%pyspark
prediction = model.transform(test)
predicted = prediction.select("wages", "prediction", "TotalWages")
predicted.show()

+--------------------+------------------+----------+
|               wages|        prediction|TotalWages|
+--------------------+------------------+----------+
|[6568.0,6568.0,0....| 6018.957673520116|      6568|
|[19543.0,19543.0,...|19280.569624496427|     19543|
|[39770.0,40292.0,...|40034.628088291385|     40292|
|[60786.0,60786.0,...|59532.515963373786|     60786|
|[64860.0,66860.0,...| 68682.88129436344|     66860|
|[67830.0,69830.0,...| 68682.88129436344|     69830|
|[67880.0,67880.0,...| 68682.88129436344|     67880|
|[68889.0,68889.0,...|   69881.399972895|     68889|
|[47598.0,47598.0,...| 46799.98856383153|     47598|
|[82537.0,84537.0,...| 86413.26886319868|     84537|
|[82995.0,82995.0,...| 86413.26886319868|     82995|
|[83103.0,85103.0,...| 86413.26886319868|     85103|
|[94090.0,94090.0,...|  98436.8277036848|     94090|
|[96892.0,98892.0,...|  98436.8277036848|     98892|
|[100192.0,107231....|111880.68191330195|    107231|
|[95013.0,96013.0,...|  98436.8277036848|     

In [0]:
#%pyspark
prediction = model.transform(test)
predicted = prediction.select("wages", "prediction", "TotalWages")
predicted.show()

+--------------------+------------------+----------+
|               wages|        prediction|TotalWages|
+--------------------+------------------+----------+
|[6568.0,6568.0,0....| 6018.957673520116|      6568|
|[19543.0,19543.0,...|19280.569624496427|     19543|
|[39770.0,40292.0,...|40034.628088291385|     40292|
|[60786.0,60786.0,...|59532.515963373786|     60786|
|[64860.0,66860.0,...| 68682.88129436344|     66860|
|[67830.0,69830.0,...| 68682.88129436344|     69830|
|[67880.0,67880.0,...| 68682.88129436344|     67880|
|[68889.0,68889.0,...|   69881.399972895|     68889|
|[47598.0,47598.0,...| 46799.98856383153|     47598|
|[82537.0,84537.0,...| 86413.26886319868|     84537|
|[82995.0,82995.0,...| 86413.26886319868|     82995|
|[83103.0,85103.0,...| 86413.26886319868|     85103|
|[94090.0,94090.0,...|  98436.8277036848|     94090|
|[96892.0,98892.0,...|  98436.8277036848|     98892|
|[100192.0,107231....|111880.68191330195|    107231|
|[95013.0,96013.0,...|  98436.8277036848|     

In [0]:
#%pyspark
predicted.show()

+--------------------+------------------+----------+
|               wages|        prediction|TotalWages|
+--------------------+------------------+----------+
|[6568.0,6568.0,0....| 6018.957673520116|      6568|
|[19543.0,19543.0,...|19280.569624496427|     19543|
|[39770.0,40292.0,...|40034.628088291385|     40292|
|[60786.0,60786.0,...|59532.515963373786|     60786|
|[64860.0,66860.0,...| 68682.88129436344|     66860|
|[67830.0,69830.0,...| 68682.88129436344|     69830|
|[67880.0,67880.0,...| 68682.88129436344|     67880|
|[68889.0,68889.0,...|   69881.399972895|     68889|
|[47598.0,47598.0,...| 46799.98856383153|     47598|
|[82537.0,84537.0,...| 86413.26886319868|     84537|
|[82995.0,82995.0,...| 86413.26886319868|     82995|
|[83103.0,85103.0,...| 86413.26886319868|     85103|
|[94090.0,94090.0,...|  98436.8277036848|     94090|
|[96892.0,98892.0,...|  98436.8277036848|     98892|
|[100192.0,107231....|111880.68191330195|    107231|
|[95013.0,96013.0,...|  98436.8277036848|     

In [0]:
#%pyspark
print("R Squared (R2) on test data = %g" % gbt_evaluator.evaluate(prediction))
gbt_evaluator = RegressionEvaluator(labelCol="TotalWages", predictionCol="prediction", metricName="rmse")
print("RMSE: %f" % gbt_evaluator.evaluate(prediction))

R Squared (R2) on test data = 0.841562
RMSE: 31006.525910


In [0]:
#%pyspark
cva = TrainValidationSplit(estimator= pipeline, evaluator=gbt_evaluator, estimatorParamMaps=paramGrid, trainRatio=0.8)


example = cva.fit(train)

In [0]:

# Transform the test data and generate predictions by applying the trained model
prediction = example.transform(test)
predicted = prediction.select("wages", "prediction", "TotalWages")
predicted.show()

+--------------------+------------------+----------+
|               wages|        prediction|TotalWages|
+--------------------+------------------+----------+
|[6568.0,6568.0,0....| 6018.957673520116|      6568|
|[19543.0,19543.0,...|19280.569624496427|     19543|
|[39770.0,40292.0,...|40034.628088291385|     40292|
|[60786.0,60786.0,...|59532.515963373786|     60786|
|[64860.0,66860.0,...| 68682.88129436344|     66860|
|[67830.0,69830.0,...| 68682.88129436344|     69830|
|[67880.0,67880.0,...| 68682.88129436344|     67880|
|[68889.0,68889.0,...|   69881.399972895|     68889|
|[47598.0,47598.0,...| 46799.98856383153|     47598|
|[82537.0,84537.0,...| 86413.26886319868|     84537|
|[82995.0,82995.0,...| 86413.26886319868|     82995|
|[83103.0,85103.0,...| 86413.26886319868|     85103|
|[94090.0,94090.0,...|  98436.8277036848|     94090|
|[96892.0,98892.0,...|  98436.8277036848|     98892|
|[100192.0,107231....|111880.68191330195|    107231|
|[95013.0,96013.0,...|  98436.8277036848|     

In [0]:
### Code break for 2020

#K12-2020

In [0]:
#%pyspark
# File location and type
file_location = "/FileStore/tables/2020_K12Education.csv"
#file_location = "/user/jdang8/2016_UniversityOfCalifornia.csv"
file_type = "csv"

# CSV options
infer_schema = "true"
first_row_is_header = "true"
delimiter = ","

# The applied options are for CSV files. For other file types, these will be ignored.
df = spark.read.format(file_type).option("inferSchema", infer_schema)\
  .option("header", first_row_is_header) \
  .option("sep", delimiter) \
  .load(file_location)

display(df)

Year EmployerType EmployerName DepartmentOrSubdivision Position ElectedOfficial Judicial OtherPositions MinPositionSalary MaxPositionSalary ReportedBaseWage RegularPay OvertimePay LumpSumPay OtherPay TotalWages DefinedBenefitPlanContribution EmployeesRetirementCostCovered DeferredCompensationPlan HealthDentalVision TotalRetirementAndHealthContribution PensionFormula EmployerURL EmployerPopulation LastUpdatedDate EmployerCounty SpecialDistrictActivities IncludesUnfundedLiability SpecialDistrictType 2020 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 59319 0 0 500 59819 2733 0 0 20704 23437 2016 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/28/2021 Alameda null false null 2020 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 59319 0 0 0 59319 2733 0 0 9008 11741 N/A https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/28/2021 Alameda null false null 2020 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 57338 0 0 2140 59478 2641 0 0 7787 10428 N/A https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/28/2021 Alameda null false null 2020 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 59319 230 0 500 60049 2733 0 0 7749 10482 N/A https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/28/2021 Alameda null false null 2020 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 59319 0 0 500 59819 2733 0 0 7329 10062 2016 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/28/2021 Alameda null false null 2020 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 1609 0 0 0 1609 74 0 0 3843 3917 2016 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/28/2021 Alameda null false null 2020 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 31605 0 0 0 31605 1456 0 0 7749 9205 2016 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/28/2021 Alameda null false null 2020 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 47539 341 0 500 48380 2191 0 0 8166 10357 2016 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/28/2021 Alameda null false null 2020 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 2 false false null 0 0 null 53807 0 0 0 53807 1521 0 0 5845 7366 2016 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/28/2021 Alameda null false null 2020 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 3 false false null 0 0 null 68977 0 0 0 68977 5600 0 0 7310 12910 1976 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/28/2021 Alameda null false null 2020 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 3 false false null 0 0 null 66000 0 0 0 66000 3017 0 0 11197 14214 N/A https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/28/2021 Alameda null false null 2020 University of California University of California, Berkeley UC - Berkeley Acad Achievement Cnslr 3 false false null 0 0 null 69000 0 0 0 69000 5602 0 0 20813 26415 2013 Tier https://ucnet.universityofcalifornia.edu/compensation-and-benefits/ null 09/28/2021 Alameda null false null 2020 University of California University of California, Berkeley UC - Berkeley

In [0]:
# Create a view or table

temp_table_name = "2020_K12Education_csv"

df.createOrReplaceTempView(temp_table_name)


In [0]:
df2 = df.drop("DepartmentOrSubdivision", "ElectedOfficial", "Judicial","OtherPositions", "DefinedBenefitPlanContribution","EmployeesRetirementCostCovered", "DeferredCompensationPlan","HealthDentalVision", "TotalRetirementAndHealthContribution","PensionFormula", "EmployerURL","EmployerPopulation","IncludesUnfundedLiability", "SpecialDistrictActivities"," IncludesUnfundedLiability","SpecialDistrictType")
df2.printSchema()

root
 |-- Year: integer (nullable = true)
 |-- EmployerType: string (nullable = true)
 |-- EmployerName: string (nullable = true)
 |-- Position: string (nullable = true)
 |-- MinPositionSalary: integer (nullable = true)
 |-- MaxPositionSalary: integer (nullable = true)
 |-- ReportedBaseWage: string (nullable = true)
 |-- RegularPay: integer (nullable = true)
 |-- OvertimePay: integer (nullable = true)
 |-- LumpSumPay: integer (nullable = true)
 |-- OtherPay: integer (nullable = true)
 |-- TotalWages: integer (nullable = true)
 |-- LastUpdatedDate: string (nullable = true)
 |-- EmployerCounty: string (nullable = true)



In [0]:
#%pyspark
df3 = df2.na.fill(value=0).na.fill("NA")
df3.show()

+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|Year|        EmployerType|        EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|
+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|2020|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|     59319|          0|         0|     500|     59819|     09/28/2021|       Alameda|
|2020|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|     59319|          0|         0|       0|   

In [0]:
splits = df3.randomSplit([0.7,0.3])
train = splits[0]
test = splits[1]
train_rows = train.count()
test_rows = test.count()
print("Training Rows:", train_rows, "Testing Rows:", test_rows)

Training Rows: 205187 Testing Rows: 87837


In [0]:
assembler = VectorAssembler(inputCols = ["RegularPay", "TotalWages","MaxPositionSalary", "MinPositionSalary"], outputCol="wages")

In [0]:
training = assembler.transform(train)
training.show()

+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+--------------------+
|Year|        EmployerType|        EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|               wages|
+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+--------------------+
|2020|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|      1609|          0|         0|       0|      1609|     09/28/2021|       Alameda|[1609.0,1609.0,0....|
|2020|University of Cal...|University of Cal...|Acad Achievement ...|               

#Random Forest Regression

In [0]:
rf = RandomForestRegressor(labelCol="TotalWages", featuresCol="wages", numTrees=10, maxDepth=5)


In [0]:
pipeline = Pipeline(stages=[assembler, rf])

In [0]:
model = pipeline.fit(train)

In [0]:
rfModel = model.stages[-1]
print(rfModel.toDebugString)

RandomForestRegressionModel: uid=RandomForestRegressor_990e2eec0bbf, numTrees=10, numFeatures=4
  Tree 0 (weight 1.0):
    If (feature 0 <= 105671.0)
     If (feature 1 <= 41022.0)
      Predict: 11747.876844009703
     Else (feature 1 > 41022.0)
      If (feature 1 <= 75306.0)
       Predict: 57710.45734586795
      Else (feature 1 > 75306.0)
       If (feature 1 <= 149065.5)
        If (feature 0 <= 94546.5)
         Predict: 87983.6094144018
        Else (feature 0 > 94546.5)
         Predict: 106418.84902172239
       Else (feature 1 > 149065.5)
        If (feature 0 <= 4.5)
         Predict: 686135.875
        Else (feature 0 > 4.5)
         Predict: 204671.91620111733
    Else (feature 0 > 105671.0)
     Predict: 193606.7584917044
  Tree 1 (weight 1.0):
    If (feature 1 <= 114539.5)
     If (feature 0 <= 37603.0)
      If (feature 0 <= 13208.5)
       Predict: 4730.966486517815
      Else (feature 0 > 13208.5)
       If (feature 1 <= 25351.5)
        Predict: 19393.008334530823


In [0]:
#importance column name can be changed

import pandas as pd
featureImp = pd.DataFrame(list(zip(assembler.getInputCols(),
rfModel.featureImportances)),
columns=["trueWages", "importance"])
featureImp.sort_values(by="importance", ascending=False)

trueWages 
 importance 
 
 
 
 
 0 
 RegularPay 
 0.527156 
 
 
 1 
 TotalWages 
 0.472844 
 
 
 2 
 MaxPositionSalary 
 0.000000 
 
 
 3 
 MinPositionSalary 
 0.000000

In [0]:
rf = RandomForestRegressor(labelCol="TotalWages",featuresCol="wages",
numTrees=10, maxDepth=5)
# Combine stages into pipeline
pipeline = Pipeline(stages=[assembler, rf])
model = pipeline.fit(train)

In [0]:
prediction = model.transform(test)
predicted = prediction.select("wages", "prediction", "TotalWages")
predicted.show()
display(predicted)

+--------------------+------------------+----------+
|               wages|        prediction|TotalWages|
+--------------------+------------------+----------+
|[31605.0,31605.0,...| 38718.46244142247|     31605|
|[5333.0,5333.0,0....| 22037.38581282198|      5333|
|[14424.0,14424.0,...| 29335.75584447417|     14424|
|[39754.0,40254.0,...| 48101.25604245749|     40254|
|[60362.0,60362.0,...|63224.802445871734|     60362|
|[65000.0,65000.0,...|63224.802445871734|     65000|
|[65000.0,65500.0,...|63224.802445871734|     65500|
|[68977.0,68977.0,...|63224.802445871734|     68977|
|[69000.0,69000.0,...|63224.802445871734|     69000|
|[83988.0,83988.0,...| 76900.38344268584|     83988|
|[84564.0,84564.0,...| 76900.38344268584|     84564|
|[99360.0,99360.0,...|  87497.1110268934|     99360|
|[95556.0,95556.0,...|  87497.1110268934|     95556|
|[107997.0,107997....| 112347.7007042487|    107997|
|[48771.0,48771.0,...|58243.817260296724|     48771|
|[65166.0,65666.0,...|63224.802445871734|     

wages prediction TotalWages Map(vectorType -> dense, length -> 4, values -> List(31605.0, 31605.0, 0.0, 0.0)) 38718.46244142247 31605 Map(vectorType -> dense, length -> 4, values -> List(5333.0, 5333.0, 0.0, 0.0)) 22037.38581282198 5333 Map(vectorType -> dense, length -> 4, values -> List(14424.0, 14424.0, 0.0, 0.0)) 29335.75584447417 14424 Map(vectorType -> dense, length -> 4, values -> List(39754.0, 40254.0, 0.0, 0.0)) 48101.25604245749 40254 Map(vectorType -> dense, length -> 4, values -> List(60362.0, 60362.0, 0.0, 0.0)) 63224.802445871734 60362 Map(vectorType -> dense, length -> 4, values -> List(65000.0, 65000.0, 0.0, 0.0)) 63224.802445871734 65000 Map(vectorType -> dense, length -> 4, values -> List(65000.0, 65500.0, 0.0, 0.0)) 63224.802445871734 65500 Map(vectorType -> dense, length -> 4, values -> List(68977.0, 68977.0, 0.0, 0.0)) 63224.802445871734 68977 Map(vectorType -> dense, length -> 4, values -> List(69000.0, 69000.0, 0.0, 0.0)) 63224.802445871734 69000 Map(vectorType -> dense, length -> 4, values -> List(83988.0, 83988.0, 0.0, 0.0)) 76900.38344268584 83988 Map(vectorType -> dense, length -> 4, values -> List(84564.0, 84564.0, 0.0, 0.0)) 76900.38344268584 84564 Map(vectorType -> dense, length -> 4, values -> List(99360.0, 99360.0, 0.0, 0.0)) 87497.1110268934 99360 Map(vectorType -> dense, length -> 4, values -> List(95556.0, 95556.0, 0.0, 0.0)) 87497.1110268934 95556 Map(vectorType -> dense, length -> 4, values -> List(107997.0, 107997.0, 0.0, 0.0)) 112347.7007042487 107997 Map(vectorType -> dense, length -> 4, values -> List(48771.0, 48771.0, 0.0, 0.0)) 58243.817260296724 48771 Map(vectorType -> dense, length -> 4, values -> List(65166.0, 65666.0, 0.0, 0.0)) 63224.802445871734 65666 Map(vectorType -> dense, length -> 4, values -> List(66997.0, 66997.0, 0.0, 0.0)) 63224.802445871734 66997 Map(vectorType -> dense, length -> 4, values -> List(69846.0, 70346.0, 0.0, 0.0)) 64041.632550556635 70346 Map(vectorType -> dense, length -> 4, values -> List(78190.0, 78690.0, 0.0, 0.0)) 74674.56947504147 78690 Map(vectorType -> dense, length -> 4, values -> List(79327.0, 81327.0, 0.0, 0.0)) 74674.56947504147 81327 Map(vectorType -> dense, length -> 4, values -> List(79415.0, 79415.0, 0.0, 0.0)) 74674.56947504147 79415 Map(vectorType -> dense, length -> 4, values -> List(80295.0, 80990.0, 0.0, 0.0)) 74674.56947504147 80990 Map(vectorType -> dense, length -> 4, values -> List(5397.0, 5397.0, 0.0, 0.0)) 22037.38581282198 5397 Map(vectorType -> dense, length -> 4, values -> List(14000.0, 14000.0, 0.0, 0.0)) 29335.75584447417 14000 Map(vectorType -> dense, length -> 4, values -> List(55293.0, 58104.0, 0.0, 0.0)) 59192.65511235197 58104 Map(vectorType -> dense, length -> 4, values -> List(55958.0, 71173.0, 0.0, 0.0)) 60883.64076101415 71173 Map(vectorType -> dense, length -> 4, values -> List(78516.0, 79016.0, 0.0, 0.0)) 74674.56947504147 79016 Map(vectorType -> dense, length -> 4, values -> List(78516.0, 79016.0, 0.0, 0.0)) 74674.56947504147 79016 Map(vectorType -> dense, length -> 4, values -> List(82704.0, 89407.0, 0.0, 0.0)) 76900.38344268584 89407 Map(vectorType -> dense, length -> 4, values -> List(88246.0, 91658.0, 0.0, 0.0)) 83481.00047198062 91658 Map(vectorType -> dense, length -> 4, values -> List(89277.0, 89777.0, 0.0, 0.0)) 82135.17638096213 89777 Map(vectorType -> dense, length -> 4, values -> List(100542.0, 108542.0, 0.0, 0.0)) 87497.1110268934 108542 Map(vectorType -> dense, length -> 4, values -> List(103308.0, 109141.0, 0.0, 0.0)) 87497.1110268934 109141 Map(vectorType -> dense, length -> 4, values -> List(32579.0, 32579.0, 0.0, 0.0)) 39326.781696356935 32579 Map(vectorType -> dense, length -> 4, values -> List(59384.0, 66261.0, 0.0, 0.0)) 61606.57923916627 66261 Map(vectorType -> dense, length -> 4, values -> List(108650.0, 110650.0, 0.0, 0.0)) 112347.7007042487 110650 Map(vectorType -> dense, length -> 4, values -> List(111372.0, 111372.0, 0.0, 0.0)) 112347.7007042487 111372 Map(vectorType -> dense, length -> 

In [0]:
    
      from pyspark.ml.evaluation import RegressionEvaluator
rf_evaluator = RegressionEvaluator(predictionCol="prediction", \
                                   labelCol="TotalWages",metricName="r2")
print("R Squared (R2) on test data = %g" % rf_evaluator.evaluate(prediction))
rf_evaluator = RegressionEvaluator(labelCol="TotalWages", predictionCol="prediction", metricName="rmse")
print("RMSE: %f" % rf_evaluator.evaluate(prediction))

R Squared (R2) on test data = 0.700948
RMSE: 44771.744477


#Gradient Boost Tree (GBT)

In [0]:
#%pyspark
df3 = df2.na.fill(value=0).na.fill("NA")
df3.show()

+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|Year|        EmployerType|        EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|
+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|2020|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|     59319|          0|         0|     500|     59819|     09/28/2021|       Alameda|
|2020|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|     59319|          0|         0|       0|   

In [0]:
#%pyspark
splits = df3.randomSplit([0.7,0.3])
train = splits[0]
test = splits[1]
train_rows = train.count()
test_rows = test.count()
print("Training Rows:", train_rows, "Testing Rows:", test_rows)

Training Rows: 205140 Testing Rows: 87884


In [0]:
#%pyspark
assembler = VectorAssembler(inputCols = ["RegularPay", "TotalWages","MaxPositionSalary", "MinPositionSalary"], outputCol="wages")

In [0]:
#%pyspark
training = assembler.transform(train)
training.show()

+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+--------------------+
|Year|        EmployerType|        EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|               wages|
+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+--------------------+
|2020|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|     31605|          0|         0|       0|     31605|     09/28/2021|       Alameda|[31605.0,31605.0,...|
|2020|University of Cal...|University of Cal...|Acad Achievement ...|               

In [0]:
#%pyspark

gbt = GBTRegressor(labelCol="TotalWages", featuresCol="wages", maxDepth=5)

In [0]:
#%pyspark
paramGrid = ParamGridBuilder()\
.addGrid(gbt.maxDepth, [2, 5])\
.addGrid(gbt.maxIter, [10, 20])\
.build()

In [0]:
#%pyspark
#gbt_evaluator = RegressionEvaluator(predictionCol="prediction", \ labelCol="TotalWages",metricName="r2")

gbt_evaluator = RegressionEvaluator(predictionCol="prediction", labelCol="TotalWages", metricName="r2")


In [0]:
#%pyspark
pipeline = Pipeline(stages=[assembler, gbt])

In [0]:
#%pyspark
cv = CrossValidator(estimator=pipeline, evaluator= gbt_evaluator, estimatorParamMaps=paramGrid)
#%pyspark
model = cv.fit(train)
#@%pyspark
test.show()


+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|Year|        EmployerType|        EmployerName|            Position|MinPositionSalary|MaxPositionSalary|ReportedBaseWage|RegularPay|OvertimePay|LumpSumPay|OtherPay|TotalWages|LastUpdatedDate|EmployerCounty|
+----+--------------------+--------------------+--------------------+-----------------+-----------------+----------------+----------+-----------+----------+--------+----------+---------------+--------------+
|2020|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|      1609|          0|         0|       0|      1609|     09/28/2021|       Alameda|
|2020|University of Cal...|University of Cal...|Acad Achievement ...|                0|                0|              NA|     53807|          0|         0|       0|   

In [0]:
#%pyspark
prediction = model.transform(test)
predicted = prediction.select("wages", "prediction", "TotalWages")
predicted.show()

+--------------------+------------------+----------+
|               wages|        prediction|TotalWages|
+--------------------+------------------+----------+
|[1609.0,1609.0,0....|1451.3189081635212|      1609|
|[53807.0,53807.0,...| 53763.71102006211|     53807|
|[57338.0,59478.0,...|61401.318364748084|     59478|
|[59319.0,59819.0,...|61401.318364748084|     59819|
|[5333.0,5333.0,0....| 4439.055080100617|      5333|
|[39754.0,40254.0,...|38890.430714395756|     40254|
|[61632.0,90400.0,...| 85962.13210334958|     90400|
|[65000.0,65500.0,...| 66144.91013867171|     65500|
|[66000.0,66000.0,...| 66144.91013867171|     66000|
|[68977.0,68977.0,...| 66144.91013867171|     68977|
|[69000.0,69000.0,...| 66144.91013867171|     69000|
|[72000.0,72000.0,...| 72255.75723957931|     72000|
|[83988.0,83988.0,...|  85904.9577999301|     83988|
|[90933.0,90933.0,...| 95628.87594153082|     90933|
|[90944.0,91444.0,...| 95628.87594153082|     91444|
|[99672.0,99672.0,...| 98105.31925848628|     

In [0]:
#%pyspark
print("R Squared (R2) on test data = %g" % gbt_evaluator.evaluate(prediction))
gbt_evaluator = RegressionEvaluator(labelCol="TotalWages", predictionCol="prediction", metricName="rmse")
print("RMSE: %f" % gbt_evaluator.evaluate(prediction))

R Squared (R2) on test data = 0.85207
RMSE: 30924.561561


In [0]:
#%pyspark
cva = TrainValidationSplit(estimator= pipeline, evaluator=gbt_evaluator, estimatorParamMaps=paramGrid, trainRatio=0.8)


example = cva.fit(train)

In [0]:

# Transform the test data and generate predictions by applying the trained model
prediction = example.transform(test)
predicted = prediction.select("wages", "prediction", "TotalWages")
predicted.show()

+--------------------+------------------+----------+
|               wages|        prediction|TotalWages|
+--------------------+------------------+----------+
|[1609.0,1609.0,0....|1451.3189081635212|      1609|
|[53807.0,53807.0,...| 53763.71102006211|     53807|
|[57338.0,59478.0,...|61401.318364748084|     59478|
|[59319.0,59819.0,...|61401.318364748084|     59819|
|[5333.0,5333.0,0....| 4439.055080100617|      5333|
|[39754.0,40254.0,...|38890.430714395756|     40254|
|[61632.0,90400.0,...| 85962.13210334958|     90400|
|[65000.0,65500.0,...| 66144.91013867171|     65500|
|[66000.0,66000.0,...| 66144.91013867171|     66000|
|[68977.0,68977.0,...| 66144.91013867171|     68977|
|[69000.0,69000.0,...| 66144.91013867171|     69000|
|[72000.0,72000.0,...| 72255.75723957931|     72000|
|[83988.0,83988.0,...|  85904.9577999301|     83988|
|[90933.0,90933.0,...| 95628.87594153082|     90933|
|[90944.0,91444.0,...| 95628.87594153082|     91444|
|[99672.0,99672.0,...| 98105.31925848628|     